In [1]:
import numpy as np
import random
import math
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set
from queue import Queue
import warnings
import sys
import json
import time
import types
import pickle
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import os

In [2]:
pd.set_option('display.max_rows', None)     # 모든 행 표시
pd.set_option('display.max_columns', None)  # 모든 열 표시
pd.set_option('display.width', None)        # 가로 폭 제한 없음
pd.set_option('display.max_colwidth', None) # 셀 내용 잘림 없이 표시

In [ ]:
pd.reset_option('display.max_rows')
pd.reset_option('display.max_columns')
pd.reset_option('display.width')
pd.reset_option('display.max_colwidth')

In [3]:
class Map(NamedTuple):
    grid: np.ndarray
    start: Union[Tuple[float, float], Tuple[float, float, float]]
    goal: Union[Tuple[float, float], Tuple[float, float, float]]
    obstacles: List[Union[Tuple[float, float, float, float], Tuple[float, float, float, float, float, float]]] # x, y, width, height or x, y, z, width, height, dimension
    size: Union[Tuple[int, int], Tuple[int, int, int]]

class PlannerResult(NamedTuple):
    success: bool
    path: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    nodes: List[Union[Tuple[float, float], Tuple[float, float, float]]]
    edges: List[Tuple[Tuple[float, ...], Tuple[float, ...]]]  # (parent, child)

class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True  # 장애물 충돌 여부 등


In [ ]:
class MapGenerator:
    def __init__(
        self,
        map_type: Literal["random", "multi_narrow", "maze"] = "random",
        map_size: Union[Tuple[int, int], Tuple[int, int, int]] = (50, 50),
        obstacle_percent: float = 0.2,
        min_obstacle_size: Union[Tuple[int, int], Tuple[int, int, int]] = (2, 2),
        max_obstacle_size: Union[Tuple[int, int], Tuple[int, int, int]] = (5, 5),
        max_obstacle_count: Optional[int] = None
    ):
        self.map_type = map_type
        self.map_size = map_size
        self.obstacle_percent = obstacle_percent
        self.obstacle_list: List[Tuple[int, ...]] = []
        self.min_size = min_obstacle_size
        self.max_size = max_obstacle_size
        self.max_count = max_obstacle_count
        self.is_3d = len(map_size) == 3
        self.map = self._init_map()
        self.start = None
        self.goal = None

    def _init_map(self):
        shape = self.map_size[::-1] if self.is_3d else (self.map_size[1], self.map_size[0])
        return np.zeros(shape, dtype=np.uint8)

    def generate(self, start: Tuple[int, ...], goal: Tuple[int, ...]) -> Dict[str, Union[np.ndarray, Tuple[int, ...], List[Tuple[int, ...]], Tuple[int, int]]]:
        self.start = start
        self.goal = goal
        tries = 0
        max_tries = 100

        while tries < max_tries:
            self.map = self._init_map()
            self.obstacle_list.clear()

            if self.map_type == "maze":
                self.map = self._generate_maze()
            elif self.map_type == "random":
                self._generate_random_obstacles(start, goal)
            elif self.map_type == "multi_narrow":
                self._generate_multi_narrow(start, goal)

            if self._path_exists(start, goal):
                return Map(
                    grid=self.map,
                    start=start,
                    goal=goal,
                    obstacles=self.obstacle_list,
                    size=self.map_size
                )
            tries += 1

        raise RuntimeError("Failed to generate a connected map after multiple attempts.")

    def _add_obstacle(self, coords: Tuple[int, ...]):
        self.obstacle_list.append(coords)

    def _path_exists(self, start, goal):
        visited = set()
        q = Queue()
        q.put(start)
        visited.add(start)

        dims = len(start)
        neighbors = [(-1,0), (1,0), (0,-1), (0,1)] if dims == 2 else \
                    [(-1,0,0),(1,0,0),(0,-1,0),(0,1,0),(0,0,-1),(0,0,1)]

        while not q.empty():
            node = q.get()
            if node == goal:
                return True

            for delta in neighbors:
                neighbor = tuple(node[i] + delta[i] for i in range(dims))
                if self._in_bounds(neighbor) and neighbor not in visited:
                    if self._is_free(neighbor):
                        visited.add(neighbor)
                        q.put(neighbor)
        return False

    def _in_bounds(self, p):
        if self.is_3d:
            z, y, x = p
            return 0 <= z < self.map.shape[0] and 0 <= y < self.map.shape[1] and 0 <= x < self.map.shape[2]
        else:
            y, x = p
            return 0 <= y < self.map.shape[0] and 0 <= x < self.map.shape[1]

    def _is_free(self, p):
        if self.is_3d:
            z, y, x = p
            return self.map[z, y, x] == 0
        else:
            y, x = p
            return self.map[y, x] == 0

    def _is_inside(self, point, x, y, z, ow, oh, od):
        px, py, *pz = point
        if z is None:
            return x <= px < x + ow and y <= py < y + oh
        else:
            pz = pz[0]
            return x <= px < x + ow and y <= py < y + oh and z <= pz < z + od

    def _generate_random_obstacles(self, start, goal):
        if self.is_3d:
            w, h, d = self.map_size
            total_voxels = w * h * d
            max_obs = int(total_voxels * self.obstacle_percent)
            count = 0
            for _ in range(10000):
                ow = random.randint(self.min_size[0], self.max_size[0])
                oh = random.randint(self.min_size[1], self.max_size[1])
                od = random.randint(self.min_size[2], self.max_size[2])
                x = random.randint(0, w - ow - 1)
                y = random.randint(0, h - oh - 1)
                z = random.randint(0, d - od - 1)
                if np.any(self.map[z:z+od, y:y+oh, x:x+ow]):
                    continue
                if self._is_inside(start, x, y, z, ow, oh, od) or self._is_inside(goal, x, y, z, ow, oh, od):
                    continue
                self.map[z:z+od, y:y+oh, x:x+ow] = 1
                self._add_obstacle((x, y, z, ow, oh, od))
                count += ow * oh * od
                if self.max_count and count >= self.max_count:
                    break
                if count >= max_obs:
                    break
        else:
            w, h = self.map_size
            total_cells = w * h
            max_obs = int(total_cells * self.obstacle_percent)
            count = 0
            for _ in range(10000):
                ow = random.randint(self.min_size[0], self.max_size[0])
                oh = random.randint(self.min_size[1], self.max_size[1])
                x = random.randint(0, w - ow - 1)
                y = random.randint(0, h - oh - 1)
                if np.any(self.map[y:y+oh, x:x+ow]):
                    continue
                if self._is_inside(start, x, y, None, ow, oh, None) or self._is_inside(goal, x, y, None, ow, oh, None):
                    continue
                self.map[y:y+oh, x:x+ow] = 1
                self._add_obstacle((x, y, ow, oh))
                count += ow * oh
                if self.max_count and count >= self.max_count:
                    break
                if count >= max_obs:
                    break

    def _generate_multi_narrow(self, start, goal):
        if self.is_3d:
            self._generate_random_obstacles(start, goal)
        else:
            w, h = self.map_size
            corridor_width = 2
            spacing = 6
            for i in range(spacing, h - spacing, spacing + corridor_width):
                self.map[i:i+spacing, :] = 1
            self._carve_corridor(start, goal)

    def _carve_corridor(self, start, goal):
        if not self.is_3d:
            y0, x0 = start[1], start[0]
            y1, x1 = goal[1], goal[0]
            for x in range(min(x0, x1), max(x0, x1)+1):
                self.map[y0, x] = 0
            for y in range(min(y0, y1), max(y0, y1)+1):
                self.map[y, x1] = 0

    def _generate_maze(self):
        width, height = self.map_size
        if width % 2 == 0: width += 1
        if height % 2 == 0: height += 1

        maze = np.ones((height, width), dtype=np.uint8)
        sx, sy = 1, 1
        maze[sy, sx] = 0

        walls = [(sx + dx, sy + dy) for dx, dy in [(-2, 0), (2, 0), (0, -2), (0, 2)]
                 if 0 < sx + dx < width and 0 < sy + dy < height]

        while walls:
            wx, wy = walls.pop(random.randint(0, len(walls) - 1))
            if maze[wy, wx] == 1:
                neighbors = [(wx + dx, wy + dy) for dx, dy in [(-2, 0), (2, 0), (0, -2), (0, 2)]
                             if 0 < wx + dx < width and 0 < wy + dy < height and maze[wy + dy, wx + dx] == 0]
                if len(neighbors) == 1:
                    nx, ny = neighbors[0]
                    maze[(wy + ny) // 2, (wx + nx) // 2] = 0
                    maze[wy, wx] = 0
                    for dx, dy in [(-2, 0), (2, 0), (0, -2), (0, 2)]:
                        nx, ny = wx + dx, wy + dy
                        if 0 < nx < width and 0 < ny < height and maze[ny, nx] == 1:
                            walls.append((nx, ny))

        return maze

In [4]:
class MapIO:
    @staticmethod
    def save_map(map_data: Map, filename: str) -> None:
        """Save Map object to a binary file."""
        with open(filename, 'wb') as f:
            pickle.dump(map_data, f)

    @staticmethod
    def load_map(filename: str) -> Map:
        """Load Map object from a binary file."""
        if not os.path.exists(filename):
            raise FileNotFoundError(f"Map file not found: {filename}")
        with open(filename, 'rb') as f:
            return pickle.load(f)

In [5]:
def visualize_map_shapes(
    map_array: np.ndarray,
    start: Optional[Tuple[int, ...]] = None,
    goal: Optional[Tuple[int, ...]] = None,
    obs:List[Tuple[int, ...]] = None,
    path: Optional[List[Tuple[float, ...]]] = None,
    nodes: Optional[List[Tuple[float, ...]]] = None,
    edges: Optional[List[Tuple[float, ...]]] = None,
    title: str = "Map Visualization"
):
    fig = go.Figure()

    if map_array.ndim == 2:
        height, width = map_array.shape
        
        for x, y, w, h in obs:
                fig.add_shape(
                    type="rect",
                    x0=x, x1=x+w, y0=y, y1=y+h,
                    fillcolor="purple",opacity=0.5,
                    line=dict(width=0)
                )

        # 방문 노드
        if nodes:
            vx, vy = zip(*nodes)
            fig.add_trace(go.Scatter(
                x=vx, y=vy, mode="markers",
                marker=dict(size=4, color="blue"),
                name="nodes"
            ))

        # 경로
        if path:
            px, py = zip(*path)
            fig.add_trace(go.Scatter(
                x=px, y=py, mode="lines+markers",
                line=dict(color="green"),
                marker=dict(size=6),
                name="Path"
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter(
                    x=[parent.position[0], child.position[0]], y=[parent.position[1], child.position[1]],
                    mode="lines",
                    line=dict(color="lightblue", width=1),
                    showlegend=False,
                    hoverinfo="skip"
                ))


        # 시작/목표
        if start:
            fig.add_trace(go.Scatter(
                x=[start[0]], y=[start[1]], mode="markers",
                marker=dict(size=10, color="red"),
                name="Start"
            ))

        if goal:
            fig.add_trace(go.Scatter(
                x=[goal[0]], y=[goal[1]], mode="markers",
                marker=dict(size=10, color="orange"),
                name="Goal"
            ))

        fig.add_shape(
            type="rect",
            x0=0, y0=0,
            x1=width, y1=height,
            line=dict(color="white", width=3),
            fillcolor="rgba(0,0,0,0)",  # 투명 내부
            layer="above"
        )

        fig.update_layout(
            title=title,
            xaxis=dict(scaleanchor="y", showgrid=False),
            # yaxis=dict(showgrid=False, autorange="reversed"),
            yaxis=dict(showgrid=False),
            height=600, width=600
        )

    elif map_array.ndim == 3:
        z, y, x = map_array.nonzero()
        x, y, z = list(x), list(y), list(z)

        # for x,y,w,h in obs:
        #     fig.add_trace(go.Mesh3d(
        #         x=x, y=y, z=z,
        #         color='black',
        #         opacity=1.0,
        #         alphahull=0,
        #         name='Obstacles'
        #     ))

        fig.add_trace(go.Mesh3d(
            x=x, y=y, z=z,
            color='black',
            opacity=1.0,
            alphahull=0,
            name='Obstacles'
        ))

        if nodes:
            vx, vy, vz = zip(*nodes)
            fig.add_trace(go.Scatter3d(
                x=vx, y=vy, z=vz,
                mode='markers',
                marker=dict(size=2, color='blue'),
                name='Visited'
            ))

        # 엣지 (연결 정보)
        if edges:
            for parent, child in edges:
                fig.add_trace(go.Scatter3d(
                    x=[parent.position[0], child.position[0]],
                    y=[parent[1].position, child.position[1]],
                    z=[parent[2].position, child.position[2]],
                    mode='lines',
                    line=dict(color='lightblue', width=2),
                    showlegend=False,
                    hoverinfo="skip"
                ))

        if path:
            px_, py_, pz_ = zip(*path)
            fig.add_trace(go.Scatter3d(
                x=px_, y=py_, z=pz_,
                mode='lines+markers',
                marker=dict(size=3, color='green'),
                name='Path'
            ))

        if start:
            fig.add_trace(go.Scatter3d(
                x=[start[0]], y=[start[1]], z=[start[2]],
                mode='markers',
                marker=dict(size=5, color='red'),
                name='Start'
            ))

        if goal:
            fig.add_trace(go.Scatter3d(
                x=[goal[0]], y=[goal[1]], z=[goal[2]],
                mode='markers',
                marker=dict(size=5, color='orange'),
                name='Goal'
            ))

        fig.update_layout(
            title=title,
            scene=dict(aspectmode='data'),
            height=700, width=700
        )

        

    fig.show()


In [ ]:
gen = MapGenerator(map_type="random", map_size=(100, 100), min_obstacle_size=(5, 5), max_obstacle_size=(15, 15), obstacle_percent=0.32)
m = gen.generate(start=(1, 1), goal=(99, 99))
visualize_map_shapes(m.grid, obs=m.obstacles, start=m.start, goal=m.goal)

In [ ]:
def generate_box_with_narrow_entry(width: int, height: int, entry_side: str = "left", entry_pos: int = 10, entry_width: int = 1) -> Map:
    grid = np.zeros((height, width), dtype=np.uint8)
    obstacles = []
    start, goal = (80,50), (50,50)
    

    grid[27:30, 52:70] = 1  
    obstacles.append((27, 52, 3, 18))
    grid[27:30, 30:48] = 1  
    obstacles.append((27, 30, 3, 18))
    
    grid[70:73, 30:70] = 1
    obstacles.append((70, 30, 3, 40))

    grid[30:70, 30:33] = 1
    obstacles.append((30, 30, 40, 3))
    grid[30:70, 67:70] = 1  
    obstacles.append((30, 67, 40, 3))


    # Obstacle extraction

    return Map(
        grid=grid,
        start=start,
        goal=goal,
        obstacles=obstacles,
        size=(width, height)
    )

In [ ]:
def generate_box_with_narrow_entry(width: int, height: int, entry_side: str = "left", entry_pos: int = 10, entry_width: int = 1) -> Map:
    grid = np.zeros((height, width), dtype=np.uint8)
    obstacles = []
    start, goal = (29,40), (90,10)
    


    grid[17:20, 20:80] = 1
    obstacles.append((17, 20, 3, 60))
    grid[37:40, 0:50] = 1
    obstacles.append((37, 0, 3, 50))
    grid[57:60, 20:100] = 1
    obstacles.append((57, 20, 3, 80))
    grid[77:80, 20:70] = 1
    obstacles.append((77, 0, 3, 80))

    grid[20:37, 47:60] = 1  
    obstacles.append((20, 47, 17, 3))
    grid[30:57, 62:65] = 1 
    obstacles.append((30, 62, 27, 3))
    grid[10:45, 80:83] = 1 
    obstacles.append((10, 80, 35, 3))
    grid[10:45, 80:83] = 1 
    obstacles.append((70, 80, 20, 3))


    # Obstacle extraction

    return Map(
        grid=grid,
        start=start,
        goal=goal,
        obstacles=obstacles,
        size=(width, height)
    )

In [ ]:
def generate_box_with_narrow_entry(width: int, height: int, entry_side: str = "left", entry_pos: int = 10, entry_width: int = 1) -> Map:
    grid = np.zeros((height, width), dtype=np.uint8)
    obstacles = []
    start, goal = (29,10), (90,80)
    
    grid[27:30, 20:80] = 1
    obstacles.append((27, 20, 3, 60))
    grid[47:50, 0:50] = 1
    obstacles.append((47, 0, 3, 50))
    grid[77:80, 20:100] = 1
    obstacles.append((77, 20, 3, 80))

    grid[30:47, 47:50] = 1  
    obstacles.append((30, 47, 17, 3))
    grid[50:77, 72:65] = 1 
    obstacles.append((50, 72, 27, 3))

    # Obstacle extraction

    return Map(
        grid=grid,
        start=start,
        goal=goal,
        obstacles=obstacles,
        size=(width, height)
    )

In [ ]:
map_obj = generate_box_with_narrow_entry(width=100, height=100, entry_side="left", entry_pos=25, entry_width=2)


In [ ]:
visualize_map_shapes(map_obj.grid, obs=map_obj.obstacles, start=map_obj.start, goal=map_obj.goal)

In [ ]:
# MapIO.save_map(map_obj, "Maze_map_easy.pkl")

In [6]:
maze_map = MapIO.load_map("Maze_map_easy.pkl")
print("Start:", maze_map.start)
print("Obstacles:", len(maze_map.obstacles))
print(maze_map.grid.shape)

Start: (29, 10)
Obstacles: 5
(100, 100)


In [ ]:
maze_map = MapIO.load_map("Maze_map.pkl")
print("Start:", maze_map.start)
print("Obstacles:", len(maze_map.obstacles))
print(maze_map.grid.shape)

In [7]:
narrow_map = MapIO.load_map("Narrow_map.pkl")
print("Start:", narrow_map.start)
print("Obstacles:", len(narrow_map.obstacles))
print(narrow_map.grid.shape)

Start: (80, 50)
Obstacles: 5
(100, 100)


In [8]:
# 불러오기
multi_obs_map = MapIO.load_map("Multi_obs_map.pkl")
print("Start:", multi_obs_map.start)
print("Obstacles:", len(multi_obs_map.obstacles))
print(multi_obs_map.grid.shape)

Start: (1, 1)
Obstacles: 35
(100, 100)


In [9]:
visualize_map_shapes(multi_obs_map.grid, obs=multi_obs_map.obstacles, start=multi_obs_map.start, goal=multi_obs_map.goal)

In [24]:
# MultiMapbenchmarker
import pandas as pd
import numpy as np
import random
import time
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any
import plotly.express as px
import math

from eoh.problems.optimization.classic_benchmark_path_planning.utils.architecture_utils import PlannerResult
class MultiMapBenchmarker:
    def __init__(
        self,
        maps: List[np.ndarray],
        name: str = "Algorithm",
        learning_mode = True,
        iter = 10,
        seed = 42,
    ):
        self.set_seed(seed)

        self.maps = maps
        self.name = name
        self.results_df: pd.DataFrame = pd.DataFrame()
        self.iter = iter
        self.learning_mode = learning_mode

        self.time_limit = 5.0
        self.success_limit = 0.8
        
        # self.time_limit = 5.0
        # self.success_limit = 0.0

        self.outputs = []

    def run(self, algorithm) -> pd.DataFrame:
        results = []
        main_start_time = time.time()
        # self.outputs = []
        # print("timeout_test")
        # time.sleep(15)
        for i, map_ in enumerate(self.maps):
            print(f"[{time.strftime('%Y.%m.%d - %H:%M:%S')}] Map {i+1}")
            for j in range(self.iter):
                start_time = time.time()
                try:
                    output = algorithm(map_)
                except Exception as e:
                    output = {"path": [], "nodes": [], "n_nodes": 0}
                end_time = time.time()
                # self.outputs.append(output)
                if isinstance(output, PlannerResult):
                    path = output.path
                    nodes = output.nodes
                    num_nodes = len(nodes)
                    success = self._is_path_valid(path, map_)
                    path_length = self._compute_path_length(path)
                    path_smoothness = self._compute_path_smoothness(path)
                elif isinstance(output, Dict):
                    path = output['path']
                    nodes = output['nodes']
                    num_nodes = len(nodes)
                    success = self._is_path_valid(path, map_)
                    path_length = self._compute_path_length(path)
                    path_smoothness = self._compute_path_smoothness(path)
                else:
                    return None, None
                
                print(f"Iteration {j+1}: Time taken: {end_time - start_time:.4f} seconds, Success: {success}")

                results.append({
                    "map_id": i,
                    "iter" : j,
                    "algorithm": self.name,
                    "success": success,
                    "time_taken": end_time - start_time,
                    "num_nodes": num_nodes,
                    "path_length": path_length,
                    "path_smoothness": path_smoothness,
                })

                time_taken_avg = np.mean([r["time_taken"] for r in results])
                success_avg = np.mean([r["success"] for r in results]) if len(results) > 6 else 1.0
                if time_taken_avg > self.time_limit:
                    print("Time taken Limit")
                    return None, None
                elif success_avg < self.success_limit:
                    print("Success Rate Limit")
                    return None, None

        print(f"Total time taken for all maps: {time.time() - main_start_time:.4f} seconds")

        self.results_df = pd.DataFrame(results)
        return self.results_df, self.get_avg()
    
    def get_results(self) -> pd.DataFrame:
        return self.outputs

    def _compute_path_length(self, path: List[Tuple[float, ...]]) -> float:
        if not path or len(path) < 2:
            return 0.0
        return sum(np.linalg.norm(np.array(path[i]) - np.array(path[i+1])) for i in range(len(path) - 1))
    
    def _is_path_valid(self, path: List[Tuple[float, ...]], map_) -> bool:
        if not path or len(path) < 2:
            return False
        
        if np.linalg.norm(np.array(path[0]) - np.array(map_.start)) > 0.5 or np.linalg.norm(np.array(path[-1]) - np.array(map_.goal)) > 0.5:
            if np.linalg.norm(np.array(path[0]) - np.array(map_.goal)) > 0.5 or np.linalg.norm(np.array(path[-1]) - np.array(map_.start)) > 0.5:
                return False
            
        is_3d = True if len(map_.size) > 2 else False
        for i in range(len(path) - 1):
            p1 = path[i]
            p2 = path[i + 1]
            if self._is_edge_in_obstacle(p1, p2, map_.obstacles, is_3d):
                return False
        return True
    
    def _is_in_obstacle(self, pos, obstacles, is_3d):
        for obs in obstacles:
            if is_3d:
                x, y, z, w, h, d = obs
                px, py, pz = pos
                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:
                    return True
            else:
                x, y, w, h = obs
                px, py = pos
                if x <= px <= x + w and y <= py <= y + h:
                    return True
        return False

    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):
        distance = math.dist(from_pos, to_pos)
        steps = max(1, int(distance / resolution))
        for i in range(steps + 1):
            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))
            if self._is_in_obstacle(interp, obstacles, is_3d):
                return True
        return False
    
    def _compute_path_smoothness(self, path: List[Tuple[float, ...]]) -> float:
        """
        Compute smoothness based on total bending angles (smaller is smoother).
        Returns a value where 1 = perfectly smooth (straight), 0 = very jagged.
        """
        if not path or len(path) < 3:
            return 1.0  # trivially smooth

        total_angle = 0.0
        for i in range(1, len(path) - 1):
            p0 = np.array(path[i - 1])
            p1 = np.array(path[i])
            p2 = np.array(path[i + 1])

            v1 = p0 - p1
            v2 = p2 - p1

            norm_v1 = np.linalg.norm(v1)
            norm_v2 = np.linalg.norm(v2)
            if norm_v1 == 0 or norm_v2 == 0:
                continue  # ignore invalid

            cosine = np.dot(v1, v2) / (norm_v1 * norm_v2)
            cosine = np.clip(cosine, -1.0, 1.0)  # numerical safety
            angle = np.arccos(cosine)
            total_angle += angle

        # Normalize to [0, 1]: smoothness = 1 / (1 + total_bend)
        return 1.0 / (1.0 + total_angle)

    def save_results(self, filename: str):
        if self.results_df.empty:
            raise RuntimeError("No results to save. Run benchmark first.")
        self.results_df.to_csv(filename, index=False)

    def plot_metrics(self, metric: str = "time_taken"):
        if self.results_df.empty:
            raise RuntimeError("No results to plot. Run benchmark first.")
        if metric not in self.results_df.columns:
            raise ValueError(f"Invalid metric: {metric}")

        fig = px.bar(
            self.results_df,
            x="map_id",
            y=metric,
            color="success",
            title=f"{self.name} - {metric} per map",
            labels={"map_id": "Map ID", metric: metric.replace('_', ' ').title()}
        )
        fig.show()

    def get_avg(self):
        if self.results_df.empty:
            raise RuntimeError("No results to save. Run benchmark first.")

        classic_summary = self.results_df.groupby('map_id').agg({
            'success': 'mean',           # 성공률
            'time_taken': 'mean',        # 평균 소요 시간
            'num_nodes': 'mean',      # 평균 노드 수
            'path_length': lambda x: x[x > 0].mean(),  # path=0 제외한 평균 경로 길이
            'path_smoothness': 'mean' # 경로 부드러움
        }).rename(columns={
            'success': 'success_rate',
            'time_taken': 'time_avg',
            'num_nodes': 'num_nodes_avg',
            'path_length': 'path_length_avg',
            'path_smoothness': 'smoothness_avg'
        }).reset_index()
        return classic_summary
    
    @staticmethod
    def get_improvement(reference_result:pd.DataFrame, results:pd.DataFrame) -> pd.DataFrame:
        improvement_df = pd.DataFrame()
        
        improvement_df['success_improvement'] = (results['success_rate'] - reference_result['success_rate']) * 100 # percent point
        improvement_df['time_improvement'] = (results['time_avg'] - reference_result['time_avg']) / reference_result['time_avg'] * -100
        improvement_df['length_improvement'] = (results['path_length_avg'] - reference_result['path_length_avg']) / reference_result['path_length_avg'] * -100
        improvement_df['smoothness_improvement'] = (results['smoothness_avg'] - reference_result['smoothness_avg']) / reference_result['smoothness_avg'] * 100

        # improvement_df['objective_score'] = (
        #     5 * improvement_df['success_improvement'] +
        #     0.3 * improvement_df['time_improvement'] +
        #     0.2 * improvement_df['length_improvement'] +
        #     0.005 * improvement_df['smoothness_improvement']
        #     )
        
        improvement_df['objective_score'] = (
            5 * improvement_df['success_improvement'] +
            0.3 * improvement_df['time_improvement'] +
            0.6 * improvement_df['length_improvement'] +
            0.005 * improvement_df['smoothness_improvement']
            )

        return improvement_df
    
    def set_seed(self, seed: int = 42):
        random.seed(seed)                    # Python random
        np.random.seed(seed)                 # NumPy
        # torch.manual_seed(seed)              # PyTorch (CPU)
        # torch.cuda.manual_seed(seed)         # PyTorch (GPU)
        # torch.cuda.manual_seed_all(seed)     # If multiple GPUs
        # torch.backends.cudnn.deterministic = True  # CUDNN 고정
        # torch.backends.cudnn.benchmark = False     # 연산 최적화 OFF

## Generate templete

In [11]:
# --- PlannerResult structure ---
class PlannerResult(NamedTuple):
    success: bool                       # Path navigation success or not
    path: List[Tuple[float, ...]]       # Final path from start to goal
    nodes: List[Node]                   # All explored nodes
    edges: List[Tuple[Node, Node]]      # Parent-child connections


# --- Node class ---
class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position        # Tuple[float, ...] → 2D: (x,y), 3D: (x,y,z)
        self.parent = parent            # Node or None
        self.cost = cost                # Path cost
        self.children = []
        self.valid = True               # For collision checking etc.

    #### Create additional methods if needed ####

# --- Main Planner ---
class Planner:
    def __init__(self, max_iter: int = 5000):
        self.max_iter = max_iter

    def plan(self, map: Map) -> PlannerResult:
        bounds = map.size                  # Tuple[int, ...]: (W,H) or (W,H,D)
        start_position = map.start         # Tuple[float, ...] (W,H) or (W,H,D)
        goal_position = map.goal           # Tuple[float, ...] (W,H) or (W,H,D)
        obstacles = map.obstacles          # Rectangular blocks: 2D=(x,y,w,h), 3D=(x,y,z,w,h,d)

        is_3d = len(bounds) == 3

        # Core data
        success_state = False # Path navigation success or not
        extracted_path: List[Tuple[float, ...]] = [] # Final path from start to goal
        nodes: List[Node] = [] # All explored nodes
        edges: List[Tuple[Node, Node]] = [] # Parent-child connections

        #### Place holder: path planning logic ####

        return PlannerResult(
            success=success_state,
            path=extracted_path,
            nodes=nodes,
            edges=edges
        )
    
    def _is_in_obstacle(self, pos, obstacles, is_3d):
        for obs in obstacles:
            if is_3d:
                x, y, z, w, h, d = obs
                px, py, pz = pos
                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:
                    return True
            else:
                x, y, w, h = obs
                px, py = pos
                if x <= px <= x + w and y <= py <= y + h:
                    return True
        return False

    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):
        distance = math.dist(from_pos, to_pos)
        steps = max(1, int(distance / resolution))
        for i in range(steps + 1):
            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))
            if self._is_in_obstacle(interp, obstacles, is_3d):
                return True
        return False

In [ ]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method_.json'

In [ ]:
result = {
    "algorithm": "Improved-RRT*-Connect",
    "algorithm_description": "Improved RRT*-Connect is a bidirectional, asymptotically optimal planner that enhances RRT*-Connect by incorporating informed heuristic sampling, adaptive step size, node rejection, and pruning. It accelerates convergence and improves success rate in narrow, obstacle-rich environments.",
    "planning_mechanism": "The planner grows two trees from start and goal using informed sampling. During expansion, it adaptively adjusts the step size near obstacles, rejects inefficient new nodes, and prunes branches that cannot contribute to an improved solution. The planner rewires nearby nodes only if doing so reduces path cost, and updates the current best path whenever a successful connection is found.",
    "code": '''
class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position
        self.parent = parent
        self.cost = cost
        self.children = []
        self.valid = True

    def add_child(self, child):
        self.children.append(child)
        child.parent = self

    def path_from_root(self):
        node, path = self, []
        while node:
            path.append(node.position)
            node = node.parent
        return path[::-1]


class Planner:
    def __init__(self, max_iter=5000, step_size=5.0, rewire_radius=15.0):
        self.max_iter = max_iter
        self.base_step = step_size
        self.rewire_radius = rewire_radius

    def plan(self, map):
        import math, random, numpy as np

        bounds = map.size
        start, goal = map.start, map.goal
        obstacles = map.obstacles
        is_3d = len(bounds) == 3
        dim = len(bounds)

        tree_a, tree_b = [Node(start)], [Node(goal)]
        nodes = [tree_a[0], tree_b[0]]
        edges = []
        success, c_best, best_path = False, float("inf"), []
        c_min = math.dist(start, goal)

        for i in range(self.max_iter):
            tree_a, tree_b = (tree_a, tree_b) if i % 2 == 0 else (tree_b, tree_a)

            sample = self._informed_sample(start, goal, c_best, c_min, bounds, dim)
            nearest = min(tree_a, key=lambda n: math.dist(n.position, sample))

            step = self._adaptive_step(nearest.position, sample, obstacles, is_3d)
            new_pos = self._steer(nearest.position, sample, step)

            if self._is_in_obstacle(new_pos, obstacles, is_3d):
                continue
            if self._is_edge_in_obstacle(nearest.position, new_pos, obstacles, is_3d):
                continue

            cost = nearest.cost + math.dist(nearest.position, new_pos)
            if cost + math.dist(new_pos, goal) >= c_best:
                continue  # pruning

            new_node = Node(new_pos, nearest, cost)
            nearest.add_child(new_node)
            tree_a.append(new_node)
            nodes.append(new_node)
            edges.append((nearest, new_node))

            near_nodes = [n for n in tree_a if math.dist(n.position, new_node.position) <= self.rewire_radius]
            for near in near_nodes:
                new_cost = new_node.cost + math.dist(new_node.position, near.position)
                if new_cost < near.cost and not self._is_edge_in_obstacle(new_node.position, near.position, obstacles, is_3d):
                    if near.parent:
                        near.parent.children.remove(near)
                        edges.remove((near.parent, near))
                    near.parent = new_node
                    near.cost = new_cost
                    new_node.add_child(near)
                    edges.append((new_node, near))

            # Try to connect to the other tree
            other_nearest = min(tree_b, key=lambda n: math.dist(n.position, new_node.position))
            connect_cost = new_node.cost + math.dist(new_node.position, other_nearest.position) + other_nearest.cost
            if connect_cost < c_best and not self._is_edge_in_obstacle(new_node.position, other_nearest.position, obstacles, is_3d):
                c_best = connect_cost
                path_a = new_node.path_from_root()
                path_b = other_nearest.path_from_root()
                best_path = path_a + path_b[::-1]
                success = True

        return PlannerResult(success=success, path=best_path, nodes=nodes, edges=edges)

    def _informed_sample(self, start, goal, c_best, c_min, bounds, dim):
        import numpy as np, math, random
        if c_best == float("inf"):
            return tuple(random.uniform(0, bounds[d]) for d in range(dim))
        x_center = [(s + g) / 2 for s, g in zip(start, goal)]
        a1 = np.array(goal) - np.array(start)
        a1 = a1 / np.linalg.norm(a1)
        M = np.outer(a1, np.eye(dim)[0])
        U, _, Vt = np.linalg.svd(M)
        C = U @ np.diag([1] * (dim - 1) + [np.linalg.det(U) * np.linalg.det(Vt)]) @ Vt
        r1 = c_best / 2
        r2 = math.sqrt(c_best**2 - c_min**2) / 2
        L = np.diag([r1] + [r2] * (dim - 1))
        while True:
            x_ball = np.random.normal(0, 1, dim)
            x_ball /= np.linalg.norm(x_ball)
            x_ball *= random.random() ** (1 / dim)
            x_rand = C @ L @ x_ball + x_center
            if all(0 <= x_rand[d] <= bounds[d] for d in range(dim)):
                return tuple(x_rand)

    def _adaptive_step(self, from_pos, to_pos, obstacles, is_3d):
        import math
        distance = math.dist(from_pos, to_pos)
        steps = max(2, int(distance))
        for i in range(1, steps + 1):
            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))
            if self._is_in_obstacle(interp, obstacles, is_3d):
                return max(self.base_step * 0.3, 1.0)
        return self.base_step

    def _steer(self, from_pos, to_pos, step):
        import math
        dist = math.dist(from_pos, to_pos)
        if dist <= step:
            return to_pos
        return tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * step / dist for d in range(len(from_pos)))

    def _is_in_obstacle(self, pos, obstacles, is_3d):
        for obs in obstacles:
            if is_3d:
                x, y, z, w, h, d = obs
                px, py, pz = pos
                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:
                    return True
            else:
                x, y, w, h = obs
                px, py = pos
                if x <= px <= x + w and y <= py <= y + h:
                    return True
        return False

    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):
        import math
        distance = math.dist(from_pos, to_pos)
        steps = max(1, int(distance / resolution))
        for i in range(steps + 1):
            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))
            if self._is_in_obstacle(interp, obstacles, is_3d):
                return True
        return False

    '''
}

# 저장
with open(json_path, "a") as f:
    json.dump(result, f, indent=4)
    f.write(",\n")

In [ ]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method.json'
with open(json_path, "r") as f:
    classic_method = json.load(f)

print(classic_method[0].keys())

In [ ]:
Instruction : Implement Improved RRT*-Connect algorithm
refer to paper : https://www.mdpi.com/1424-8220/25/8/2364

!!!!!generate Only class Node and Planner!!!!!!
# --- Node class ---
class Node:
    def __init__(self, position, parent=None, cost=0.0):
        self.position = position        # Tuple[float, ...] → 2D: (x,y), 3D: (x,y,z)
        self.parent = parent            # Node or None
        self.cost = cost                # Path cost
        self.children = []
        self.valid = True               # For collision checking etc.

    #### Create additional methods if needed ####

# --- PlannerResult structure ---
class PlannerResult(NamedTuple):
    success: bool                       # Path navigation success or not
    path: List[Tuple[float, ...]]       # Final path from start to goal
    nodes: List[Node]                   # All explored nodes
    edges: List[Tuple[Node, Node]]      # Parent-child connections

# --- Main Planner ---
class Planner:
    def __init__(self, max_iter: int = 5000, step_size: float=5.0):
        self.max_iter = max_iter
        self.step_size = step_size

    def plan(self, map: Map) -> PlannerResult:
        bounds = map.size                  # Tuple[int, ...]: (W,H) or (W,H,D)
        start_position = map.start         # Tuple[float, ...] (W,H) or (W,H,D)
        goal_position = map.goal           # Tuple[float, ...] (W,H) or (W,H,D)
        obstacles = map.obstacles          # Rectangular blocks: 2D=(x,y,w,h), 3D=(x,y,z,w,h,d)

        is_3d = len(bounds) == 3

        # Core data
        success_state = False # Path navigation success or not
        extracted_path: List[Tuple[float, ...]] = [] # Final path from start to goal
        nodes: List[Node] = [] # All explored nodes
        edges: List[Tuple[Node, Node]] = [] # Parent-child connections

        #### Place holder: path planning logic ####

        return PlannerResult(
            success=success_state,
            path=extracted_path,
            nodes=nodes,
            edges=edges
        )

    def _is_in_obstacle(self, pos, obstacles, is_3d):
        for obs in obstacles:
            if is_3d:
                x, y, z, w, h, d = obs
                px, py, pz = pos
                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:
                    return True
            else:
                x, y, w, h = obs
                px, py = pos
                if x <= px <= x + w and y <= py <= y + h:
                    return True
        return False

    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):
        distance = math.dist(from_pos, to_pos)
        steps = max(1, int(distance / resolution))
        for i in range(steps + 1):
            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * (i / steps) for d in range(len(from_pos)))
            if self._is_in_obstacle(interp, obstacles, is_3d):
                return True
        return False
    

### Constraints:
- Implement it in Python.
- You DO NOT NEED to declare the any imports.
- When connecting nodes and adding edges in the planner, always perform two critical checks:
1.Collision check for the node position: Ensure that the new node itself does not lie inside any obstacle.
2.Edge-obstacle intersection check: Before adding an edge between two nodes, verify that the straight-line path between them does not intersect or pass through any obstacle.
- DO NOT OVER MAP BOUND
- After code generation, you must review the code to ensure it is syntactically correct, logically coherent, and executable within the expected environment.
- At the top of your response, write an description of the algorithm in curly braces {}, followed by a concise explanation of the planning mechanism in angle brackets <>.
- Both the description and the planning mechanism should be placed outside and above the code block.
- Output the code block containing the implementation only.
⚠️ You must enforce a maximum execution time of 30 seconds for the path planning process. If the time limit is exceeded, the algorithm must immediately stop searching and return the best-found path so far, along with a status indicating that the time limit was reached.
⚠️ Do not give additional explanations.


In [ ]:
filtered_sorted_algorithms[0].keys()

In [ ]:
for alg in classic_method:
    if alg['algorithm'] == 'BI-RRT*':
        print("alg load")
        result = alg

In [ ]:
for alg in filtered_sorted_algorithms:
    if alg['objective'] == -4.59249:
        print("alg load")
        result = alg

code_string = result['code']
with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    planning_module = types.ModuleType("planning_module")
    exec(import_string+code_string, planning_module.__dict__)
    sys.modules[planning_module.__name__] = planning_module
    p = planning_module.Planner(max_iter=5000, step_size=5.0)


In [ ]:
p = Planner(max_iter=5000, step_size=5)
# p = planning_module.Planner()

In [ ]:
result = p.plan(map=multi_obs_map)

In [ ]:
result2 = p.plan(map=maze_map)

In [ ]:
result3 = p.plan(map=narrow_map)

In [ ]:
visualize_map_shapes(multi_obs_map.grid, obs=multi_obs_map.obstacles, start=multi_obs_map.start, goal=multi_obs_map.goal,
                      path=result.path, nodes=list(map(lambda x: x.position, result.nodes)), edges=result.edges)

In [ ]:
visualize_map_shapes(maze_map.grid, obs=maze_map.obstacles, start=maze_map.start, goal=maze_map.goal, path=result2.path, nodes=list(map(lambda x: x.position, result2.nodes)), edges=result2.edges)

In [ ]:
visualize_map_shapes(narrow_map.grid, obs=narrow_map.obstacles, start=narrow_map.start, goal=narrow_map.goal, path=result3.path, nodes=list(map(lambda x: x.position, result3.nodes)), edges=result3.edges)

In [ ]:
bench2 = MultiMapBenchmarker(
    maps=[multi_obs_map, maze_map, narrow_map],
    name="MyRRT"
)
_, avg_res = bench2.run(p.plan)

In [ ]:
def my_dummy_planner(map_array, start, goal):
    return {
        "path": [start, goal],
        "visited": [start],
        "nodes": 2
    }

bench = MultiMapBenchmarker(
    maps=[multi_obs_map, maze_map, narrow_map],
    algorithm=p.plan,
    name="MyRRT"
)


df = bench.run()
print(df)

In [12]:
import_string ='''
from typing import Tuple, Literal, Union, Optional, List, Dict, NamedTuple, Callable, Any, Set, TYPE_CHECKING, Type
import time
from queue import Queue
import numpy as np
import random
import math
import sys
import os
from eoh.problems.optimization.classic_benchmark_path_planning.utils.architecture_utils import PlannerResult, Map

'''

In [13]:
def get_exp_result(path, ref_avg):
    with open(path, "r") as f:
        data = json.load(f)
        filtered_sorted_algorithms = sorted(
        [alg for alg in data if alg.get('operator') != 'initial'],
        key=lambda x: x.get('objective', float('inf'))
        )

    len(filtered_sorted_algorithms)

    # ref_avg 앞에서 선언됨
    maps = [multi_obs_map, maze_map, narrow_map]
    benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

    g_total_df = pd.DataFrame()

    for method in filtered_sorted_algorithms:
        code_string = method['code']
        namedf = pd.DataFrame()
        namedf['alg_name'] = [method['objective']]* len(maps)
        with warnings.catch_warnings():
            warnings.simplefilter("ignore")
            planning_module = types.ModuleType("planning_module")
            exec(import_string+code_string, planning_module.__dict__)
            sys.modules[planning_module.__name__] = planning_module
            try:
                planner = planning_module.Planner(max_iter=5000)
            except:
                continue
            res, avg_rest = benchmarker.run(planner.plan)

            if avg_rest is None: continue
            imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

            res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
            g_total_df = pd.concat([g_total_df, res_df], axis=0)

    return g_total_df

In [14]:
json_path = './eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/classic_method__.json'
with open(json_path, "r") as f:
    classic_method = json.load(f)

print(classic_method[0].keys())

dict_keys(['algorithm', 'algorithm_description', 'planning_mechanism', 'code'])


In [20]:
[x['algorithm'] for x in classic_method]

['RRT',
 'RRT*',
 'RRT-Connect',
 'RRT*-Connect',
 'BI-RRT',
 'BI-RRT*',
 'Informed-RRT*',
 'Informed-RRT*-Connect',
 'Bidirectional-Informed-RRT*',
 'Improved-RRT*-Connect']

In [ ]:
for method in classic_method:
    if method['algorithm'] == 'RRT':
        print(method['code'])

In [25]:
maps = [multi_obs_map, maze_map, narrow_map]
benchmarker = MultiMapBenchmarker(maps=maps, iter=100)

total_df = pd.DataFrame()

for method in classic_method:
    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['algorithm']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        planner = planning_module.Planner(max_iter=5000)
        res, avg_rest = benchmarker.run(planner.plan)
        if method['algorithm'] == 'RRT':
            ref_avg = avg_rest
            
        if avg_rest is None: continue
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        total_df = pd.concat([total_df, res_df], axis=0)

total_df


[2025.09.15 - 15:20:26] Map 1
Iteration 1: Time taken: 0.0178 seconds, Success: True
Iteration 2: Time taken: 0.0228 seconds, Success: True
Iteration 3: Time taken: 0.0197 seconds, Success: True
Iteration 4: Time taken: 0.0100 seconds, Success: True
Iteration 5: Time taken: 0.0235 seconds, Success: True
Iteration 6: Time taken: 0.0105 seconds, Success: True
Iteration 7: Time taken: 0.0123 seconds, Success: True
Iteration 8: Time taken: 0.0497 seconds, Success: True
Iteration 9: Time taken: 0.0184 seconds, Success: True
Iteration 10: Time taken: 0.0670 seconds, Success: True
Iteration 11: Time taken: 0.0190 seconds, Success: True
Iteration 12: Time taken: 0.0323 seconds, Success: True
Iteration 13: Time taken: 0.0129 seconds, Success: True
Iteration 14: Time taken: 0.0594 seconds, Success: True
Iteration 15: Time taken: 0.0301 seconds, Success: True
Iteration 16: Time taken: 0.0157 seconds, Success: True
Iteration 17: Time taken: 0.0178 seconds, Success: True
Iteration 18: Time taken: 0

alg_name  map_id  success_rate  time_avg  num_nodes_avg  \
0                          RRT       0           1.0  0.033823         461.98   
1                          RRT       1           1.0  0.207221        1637.59   
2                          RRT       2           1.0  0.073402         859.41   
0                         RRT*       0           1.0  0.074257         447.98   
1                         RRT*       1           1.0  0.434121        1630.00   
2                         RRT*       2           1.0  0.130428         796.67   
0                  RRT-Connect       0           1.0  0.008769         106.12   
1                  RRT-Connect       1           1.0  0.015405         236.56   
2                  RRT-Connect       2           1.0  0.020026         251.01   
0                 RRT*-Connect       0           1.0  0.011755         129.62   
1                 RRT*-Connect       1           1.0  0.019660         263.17   
2                 RRT*-Connect       2           1.0  0.029110         288.33   
0                       BI-RRT       0           1.0  0.003097          72.90   
1                       BI-RRT       1           1.0  0.009152         228.86   
2                       BI-RRT       2           1.0  0.007935         163.75   
0                      BI-RRT*       0           1.0  0.019107          83.31   
1                      BI-RRT*       1           1.0  0.034715         240.33   
2                      BI-RRT*       2           1.0  0.029940         203.75   
0                Informed-RRT*       0           1.0  0.298353         726.89   
1                Informed-RRT*       1           1.0  0.363161        1218.83   
2                Informed-RRT*       2           1.0  0.191767         845.48   
0        Informed-RRT*-Connect       0           1.0  0.816801         471.14   
1        Informed-RRT*-Connect       1           1.0  0.451693         589.12   
2        Informed-RRT*-Connect       2           1.0  0.642705         563.16   
0  Bidirectional-Informed-RRT*       0           1.0  0.199972         440.85   
1  Bidirectional-Informed-RRT*       1           1.0  0.104953         508.97   
2  Bidirectional-Informed-RRT*       2           1.0  0.146902         551.00   
0        Improved-RRT*-Connect       0           1.0  0.146090         334.00   
1        Improved-RRT*-Connect       1           1.0  0.142303         644.38   
2        Improved-RRT*-Connect       2           1.0  0.149662         578.11   

   path_length_avg  smoothness_avg  success_improvement  time_improvement  \
0       188.080816        0.006254                  0.0         -0.000000   
1       303.968509        0.003852                  0.0         -0.000000   
2       150.713378        0.007887                  0.0         -0.000000   
0       157.771191        0.014527                  0.0       -119.546490   
1       225.665909        0.011059                  0.0       -109.496706   
2       116.530178        0.021042                  0.0        -77.690890   
0       195.985942        0.011055                  0.0         74.073562   
1       302.131675        0.007242                  0.0         92.566098   
2       160.833474        0.014351                  0.0         72.717772   
0       171.903015        0.016822                  0.0         65.245987   
1       258.288269        0.011071                  0.0         90.512655   
2       133.799123        0.021584                  0.0         60.341408   
0       179.646964        0.010684                  0.0         90.842657   
1       305.361103        0.006401                  0.0         95.583505   
2       156.816038        0.013011                  0.0         89.189249   
0       165.592398        0.018017                  0.0         43.507665   
1       264.277359        0.010454                  0.0         83.247567   
2       130.651560        0.022292                  0.0         59.210064   
0       149.971162        0.029144             

In [26]:
# classic method result
grouped_avg = total_df.groupby('alg_name').mean()
a = pd.DataFrame(grouped_avg)
a

map_id  success_rate  time_avg  num_nodes_avg  \
alg_name                                                                     
BI-RRT                          1.0           1.0  0.006728     155.170000   
BI-RRT*                         1.0           1.0  0.027921     175.796667   
Bidirectional-Informed-RRT*     1.0           1.0  0.150609     500.273333   
Improved-RRT*-Connect           1.0           1.0  0.146018     518.830000   
Informed-RRT*                   1.0           1.0  0.284427     930.400000   
Informed-RRT*-Connect           1.0           1.0  0.637066     541.140000   
RRT                             1.0           1.0  0.104815     986.326667   
RRT*                            1.0           1.0  0.212935     958.216667   
RRT*-Connect                    1.0           1.0  0.020175     227.040000   
RRT-Connect                     1.0           1.0  0.014733     197.896667   

                             path_length_avg  smoothness_avg  \
alg_name                                                       
BI-RRT                            213.941368        0.010032   
BI-RRT*                           186.840439        0.016921   
Bidirectional-Informed-RRT*       171.859631        0.029741   
Improved-RRT*-Connect             170.811093        0.030153   
Informed-RRT*                     161.982690        0.030676   
Informed-RRT*-Connect             165.450936        0.044705   
RRT                               214.254234        0.005997   
RRT*                              166.655759        0.015543   
RRT*-Connect                      187.996802        0.016492   
RRT-Connect                       219.650364        0.010883   

                             success_improvement  time_improvement  \
alg_name                                                             
BI-RRT                                       0.0         91.871804   
BI-RRT*                                      0.0         61.988432   
Bidirectional-Informed-RRT*                  0.0       -180.671264   
Improved-RRT*-Connect                        0.0       -134.830779   
Informed-RRT*                                0.0       -339.537704   
Informed-RRT*-Connect                        0.0      -1069.504647   
RRT                                          0.0          0.000000   
RRT*                                         0.0       -102.244695   
RRT*-Connect                                 0.0         72.033350   
RRT-Connect                                  0.0         79.785811   

                             length_improvement  smoothness_improvement  \
alg_name                                                                  
BI-RRT                                -0.007719               67.326861   
BI-RRT*                               12.775225              180.716786   
Bidirectional-Informed-RRT*           19.815096              389.512360   
Improved-RRT*-Connect                 19.889434              394.092078   
Informed-RRT*                         23.838074              415.824461   
Informed-RRT*-Connect                 22.505155              634.562555   
RRT                                    0.000000                0.000000   
RRT*                                  21.518749              162.073757   
RRT*-Connect                          11.617421              176.692995   
RRT-Connect                           -3.437853               82.246663   

                             objective_score  
alg_name                                      
BI-RRT                             27.893544  
BI-RRT*                            27.165249  
Bidirectional-Informed-RRT*       -40.364760  
Improved-RRT*-Connect             -26.545113  
Informed-RRT*                     -85.479344  
Informed-RRT*-Connect            -304.175488  
RRT                                 0.000000  
RRT*                              -16.951790  
RRT*-Connect                       29.463922  
RRT-Connect                        22.284265

In [ ]:
(986.32- 622.96)/986.32

In [ ]:
# expert eoh1
pop_path = "./path_planning/mobj/results/pops/population_generation_9.json"

with open(pop_path, "r") as f:
    data = json.load(f)
    filtered_sorted_algorithms = sorted(
    [alg for alg in data if alg.get('operator') != 'initial'],
    key=lambda x: x.get('objective', float('inf'))
    )

In [ ]:
len(filtered_sorted_algorithms)

In [27]:
pop_path = "./path_planning/mobj/results/pops/population_generation_9.json"

# g_total_df
res1 = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:30:25] Map 1
Iteration 1: Time taken: 0.0085 seconds, Success: True
Iteration 2: Time taken: 0.0030 seconds, Success: True
Iteration 3: Time taken: 0.0020 seconds, Success: True
Iteration 4: Time taken: 0.0031 seconds, Success: True
Iteration 5: Time taken: 0.0030 seconds, Success: True
Iteration 6: Time taken: 0.0055 seconds, Success: True
Iteration 7: Time taken: 0.0020 seconds, Success: True
Iteration 8: Time taken: 0.0075 seconds, Success: True
Iteration 9: Time taken: 0.0030 seconds, Success: True
Iteration 10: Time taken: 0.0045 seconds, Success: True
Iteration 11: Time taken: 0.0040 seconds, Success: True
Iteration 12: Time taken: 0.0025 seconds, Success: True
Iteration 13: Time taken: 0.0010 seconds, Success: True
Iteration 14: Time taken: 0.0040 seconds, Success: True
Iteration 15: Time taken: 0.0040 seconds, Success: True
Iteration 16: Time taken: 0.0160 seconds, Success: True
Iteration 17: Time taken: 0.0030 seconds, Success: True
Iteration 18: Time taken: 0

In [ ]:
whole_df = pd.concat([total_df, g_total_df], axis=0)

In [28]:
grouped_avg = res1.groupby('alg_name').mean()
res1_ = pd.DataFrame(grouped_avg)
res1_

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-15.03871     1.0      1.000000  0.013586     190.490000       206.028841   
-14.13591     1.0      1.000000  0.012360     176.363333       196.179998   
-11.35589     1.0      1.000000  0.015357     153.813333       201.804209   
-10.57241     1.0      1.000000  0.016677     137.973333       179.935385   
-9.55661      1.0      1.000000  0.012733     177.280000       195.900211   
-9.23875      1.0      1.000000  0.014476     200.010000       205.336016   
-8.93552      1.0      1.000000  0.014713     192.553333       197.893975   
-7.55322      1.0      1.000000  0.014913     144.276667       179.050676   
-6.95653      1.0      1.000000  0.019805     143.463333       176.402730   
-6.83895      1.0      1.000000  0.017978     147.726667       178.011394   
-6.77813      1.0      1.000000  0.015230     193.260000       202.078097   
-6.68311      1.0      0.903333  0.013906     199.010000       184.039499   
-6.65759      1.0      1.000000  0.015548     169.883333       181.619253   
-6.65571      1.0      0.996667  0.021198     311.496667       177.780575   
-6.52887      1.0      1.000000  0.026003     151.533333       175.995172   
-6.33180      1.0      1.000000  0.016274     186.743333       173.716691   
-6.15402      1.0      1.000000  0.015359     158.466667       202.092832   
-6.02303      1.0      1.000000  0.018404     149.080000       177.898852   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-15.03871        0.010916             0.000000         84.473449   
-14.13591        0.014301             0.000000         84.977883   
-11.35589        0.012024             0.000000         81.498523   
-10.57241        0.070191             0.000000         77.996057   
-9.55661         0.013567             0.000000         84.430062   
-9.23875         0.010811             0.000000         83.272262   
-8.93552         0.013310             0.000000         82.995290   
-7.55322         0.060041             0.000000         81.462909   
-6.95653         0.069332             0.000000         75.178124   
-6.83895         0.071422             0.000000         77.723080   
-6.77813         0.011977             0.000000         81.854853   
-6.68311         0.016939            -9.666667         82.530728   
-6.65759         0.057340             0.000000         81.021321   
-6.65571         0.053639            -0.333333         75.064311   
-6.52887         0.069316             0.000000         69.366548   
-6.33180         0.105542             0.000000         79.218221   
-6.15402         0.012069             0.000000         81.618574   
-6.02303         0.067780             0.000000         77.246574   

           length_improvement  smoothness_improvement  objective_score  
alg_name                                                                
-15.03871            4.074372               80.563377        28.189475  
-14.13591            8.689853              134.946364        31.382009  
-11.35589            5.766003               99.064673        28.404482  
-10.57241           15.262384             1156.777024        38.340133  
-9.55661             8.631778              123.622219        31.126197  
-9.23875             4.095511               79.589660        27.836934  
-8.93552             7.762752              119.096000        30.151718  
-7.55322            15.944082              951.180565        38.761225  
-6.95653            16.955935             1143.189136        38.442944  
-6.83895            16.186956             1203.831753        39.048257  
-6.77813             5.791559               98.319088        28.522987  
-6.68311            14.087391              177.283261       -14.235264  
-6.65759            14.631428              902.556365        37.598035  
-6.65571      

In [29]:
pop_path = "./path_planning/mobj1/results/pops/population_generation_10.json"
res2 = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:32:46] Map 1
Iteration 1: Time taken: 0.0155 seconds, Success: True
Iteration 2: Time taken: 0.0055 seconds, Success: True
Iteration 3: Time taken: 0.0085 seconds, Success: True
Iteration 4: Time taken: 0.0071 seconds, Success: True
Iteration 5: Time taken: 0.0060 seconds, Success: True
Iteration 6: Time taken: 0.0080 seconds, Success: True
Iteration 7: Time taken: 0.0075 seconds, Success: True
Iteration 8: Time taken: 0.0089 seconds, Success: True
Iteration 9: Time taken: 0.0040 seconds, Success: True
Iteration 10: Time taken: 0.0060 seconds, Success: True
Iteration 11: Time taken: 0.0060 seconds, Success: True
Iteration 12: Time taken: 0.0061 seconds, Success: True
Iteration 13: Time taken: 0.0058 seconds, Success: True
Iteration 14: Time taken: 0.0050 seconds, Success: True
Iteration 15: Time taken: 0.0071 seconds, Success: True
Iteration 16: Time taken: 0.0065 seconds, Success: True
Iteration 17: Time taken: 0.0100 seconds, Success: True
Iteration 18: Time taken: 0

In [30]:
grouped_avg = res2.groupby('alg_name').mean()
res2_ = pd.DataFrame(grouped_avg)
res2_

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-11.12807     1.0           1.0  0.014099     150.463333       178.275987   
-7.23208      1.0           1.0  0.016029     150.246667       175.065409   
-7.12118      1.0           1.0  0.015954     149.833333       179.089798   
-6.46310      1.0           1.0  0.016572     157.380000       174.771384   
-6.37314      1.0           1.0  0.019051     151.493333       174.228680   
-5.84788      1.0           1.0  0.016850     152.026667       175.898703   
-5.82745      1.0           1.0  0.017618     149.800000       174.655085   
-5.68873      1.0           1.0  0.016032     150.620000       175.506817   
-4.59249      1.0           1.0  0.016822     151.350000       179.261070   
-4.01111      1.0           1.0  0.017861     150.913333       173.911071   
-3.83430      1.0           1.0  0.019008     151.863333       173.173781   
-3.32505      1.0           1.0  0.019153     153.273333       174.061685   
-2.91188      1.0           1.0  0.018531     152.253333       174.053331   
-2.73225      1.0           1.0  0.022026     160.663333       174.822410   
-2.43652      1.0           1.0  0.019576     156.636667       175.079499   
-2.05071      1.0           1.0  0.016763     150.816667       173.064249   
-1.99103      1.0           1.0  0.017590     150.656667       174.416150   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-11.12807        0.065757                  0.0         82.752905   
-7.23208         0.068300                  0.0         79.780436   
-7.12118         0.064162                  0.0         80.193280   
-6.46310         0.092487                  0.0         79.007153   
-6.37314         0.090764                  0.0         75.319536   
-5.84788         0.068867                  0.0         78.613950   
-5.82745         0.087632                  0.0         77.970751   
-5.68873         0.071090                  0.0         79.930208   
-4.59249         0.068966                  0.0         78.952712   
-4.01111         0.088415                  0.0         77.222695   
-3.83430         0.091802                  0.0         75.865662   
-3.32505         0.084785                  0.0         75.699532   
-2.91188         0.086098                  0.0         77.370661   
-2.73225         0.081816                  0.0         72.235778   
-2.43652         0.084627                  0.0         75.531488   
-2.05071         0.087551                  0.0         78.384431   
-1.99103         0.081579                  0.0         78.390476   

           length_improvement  smoothness_improvement  objective_score  
alg_name                                                                
-11.12807           16.003056             1039.730273        39.626357  
-7.23208            17.512948             1097.411463        39.928957  
-7.12118            15.657992              996.836520        38.436962  
-6.46310            17.849513             1597.327534        42.398492  
-6.37314            17.964819             1580.438571        41.276945  
-5.84788            17.015470             1127.780054        39.432367  
-5.82745            17.756065             1493.730385        41.513516  
-5.68873            17.314961             1147.640995        40.106244  
-4.59249            15.601277             1121.032218        38.651741  
-4.01111            18.021195             1498.248651        41.470769  
-3.83430            18.465603             1592.628594        41.802204  
-3.32505            17.975648             1449.811178        40.744304  
-2.91188            18.065299             1473.616761        41.418462  
-2.73225            17.514325             1409.532036        39.226988  
-2.43652            17.545925             1478.400816        40.579006  
-2.05071     

In [31]:
pop_path = "./path_planning/exp_result/basic_eoh_from_ma.json"
res3 = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:34:19] Map 1
Iteration 1: Time taken: 0.0040 seconds, Success: True
Iteration 2: Time taken: 0.0095 seconds, Success: True
Iteration 3: Time taken: 0.0055 seconds, Success: True
Iteration 4: Time taken: 0.0135 seconds, Success: True
Iteration 5: Time taken: 0.0060 seconds, Success: True
Iteration 6: Time taken: 0.0075 seconds, Success: True
Iteration 7: Time taken: 0.0050 seconds, Success: True
Iteration 8: Time taken: 0.0040 seconds, Success: True
Iteration 9: Time taken: 0.0075 seconds, Success: True
Iteration 10: Time taken: 0.0082 seconds, Success: True
Iteration 11: Time taken: 0.0085 seconds, Success: True
Iteration 12: Time taken: 0.0075 seconds, Success: True
Iteration 13: Time taken: 0.0114 seconds, Success: True
Iteration 14: Time taken: 0.0085 seconds, Success: True
Iteration 15: Time taken: 0.0070 seconds, Success: True
Iteration 16: Time taken: 0.0040 seconds, Success: True
Iteration 17: Time taken: 0.0085 seconds, Success: True
Iteration 18: Time taken: 0

In [32]:
grouped_avg = res3.groupby('alg_name').mean()
res3_ = pd.DataFrame(grouped_avg)
res3_

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-7.79662      1.0      1.000000  0.019907     399.493333       209.646352   
-0.27647      1.0      1.000000  0.024660     437.833333       178.014682   
 1.22143      1.0      1.000000  0.019192     235.353333       216.995383   
 2.98769      1.0      0.960000  0.022518     334.173333       181.929673   
 3.05605      1.0      0.970000  0.024475     255.880000       179.092539   
 4.24450      1.0      0.993333  0.023036     380.126667       180.605639   
 9.62493      1.0      0.963333  0.025163     245.550000       183.399401   
 10.51996     1.0      0.970000  0.023751     256.083333       180.257550   
 10.56800     1.0      0.966667  0.023441     241.620000       179.547162   
 11.19606     1.0      0.986667  0.030279     242.356667       184.071963   
 13.19292     1.0      0.963333  0.032164     291.626667       173.728791   
 13.86995     1.0      0.973333  0.029557     290.700000       178.590476   
 15.19604     1.0      0.960000  0.030529     245.370000       182.775344   
 16.34412     1.0      0.996667  0.020726     368.833333       180.573889   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-7.79662         0.010898             0.000000         73.112494   
-0.27647         0.023868             0.000000         68.499871   
 1.22143         0.010061             0.000000         75.095544   
 2.98769         0.029984            -4.000000         73.248840   
 3.05605         0.084239            -3.000000         64.854683   
 4.24450         0.021830            -0.666667         69.498351   
 9.62493         0.057765            -3.666667         64.265107   
 10.51996        0.079663            -3.000000         66.935549   
 10.56800        0.080625            -3.333333         66.795444   
 11.19606        0.045178            -1.333333         56.630484   
 13.19292        0.067146            -3.666667         55.349175   
 13.86995        0.067839            -2.666667         59.751631   
 15.19604        0.080647            -4.000000         54.011689   
 16.34412        0.021994            -0.333333         71.634546   

           length_improvement  smoothness_improvement  objective_score  
alg_name                                                                
-7.79662             1.659915               81.559675        23.337496  
-0.27647            16.254316              300.958834        31.807345  
 1.22143            -1.786302               68.307099        21.798418  
 2.98769            14.680195              420.832566        12.886932  
 3.05605            15.470311             1417.448711        20.825835  
 4.24450            14.958391              265.551148        27.818962  
 9.62493            13.526787              914.188727        13.633215  
 10.51996           14.887401             1343.888662        20.732549  
 10.56800           15.295316             1345.706545        19.277689  
 11.19606           13.149548              689.344581        21.658930  
 13.19292           18.304241             1087.177510        14.689851  
 13.86995           15.740203             1097.347452        19.523015  
 15.19604           13.455163             1340.511434        10.979162  
 16.34412           15.081761              268.501811        30.215263

In [33]:
pop_path = "./path_planning/mobj_analysis/results/pops/population_generation_15.json"

res4 = get_exp_result(pop_path, ref_avg)


[2025.09.15 - 15:36:08] Map 1
Iteration 1: Time taken: 0.0081 seconds, Success: True
Iteration 2: Time taken: 0.0085 seconds, Success: True
Iteration 3: Time taken: 0.0116 seconds, Success: True
Iteration 4: Time taken: 0.0071 seconds, Success: True
Iteration 5: Time taken: 0.0115 seconds, Success: True
Iteration 6: Time taken: 0.0082 seconds, Success: True
Iteration 7: Time taken: 0.0102 seconds, Success: True
Iteration 8: Time taken: 0.0136 seconds, Success: True
Iteration 9: Time taken: 0.0145 seconds, Success: True
Iteration 10: Time taken: 0.0085 seconds, Success: True
Iteration 11: Time taken: 0.0175 seconds, Success: True
Iteration 12: Time taken: 0.0128 seconds, Success: True
Iteration 13: Time taken: 0.0080 seconds, Success: True
Iteration 14: Time taken: 0.0129 seconds, Success: True
Iteration 15: Time taken: 0.0072 seconds, Success: True
Iteration 16: Time taken: 0.0065 seconds, Success: True
Iteration 17: Time taken: 0.0100 seconds, Success: True
Iteration 18: Time taken: 0

In [34]:
grouped_avg = res4.groupby('alg_name').mean()
res4_ = pd.DataFrame(grouped_avg)
res4_

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-30.22802     1.0      1.000000  0.019995     178.890000       172.272975   
-29.71144     1.0      0.950000  0.018199     212.963333       171.171965   
-29.43364     1.0      1.000000  0.016670     173.316667       174.881976   
-29.37349     1.0      1.000000  0.018431     174.963333       174.876281   
-28.86429     1.0      1.000000  0.019811     187.816667       173.992295   
-28.18988     1.0      1.000000  0.018125     185.733333       175.251277   
-28.11571     1.0      1.000000  0.024995     237.686667       174.230273   
-28.07081     1.0      1.000000  0.021320     188.423333       172.496103   
-27.62859     1.0      1.000000  0.017620     190.186667       173.824895   
-27.52708     1.0      1.000000  0.019337     179.670000       173.781344   
-27.44347     1.0      1.000000  0.018986     180.173333       174.883445   
-27.23958     1.0      1.000000  0.020666     179.606667       172.820324   
-27.12699     1.0      1.000000  0.019270     190.190000       176.008898   
-26.71132     1.0      1.000000  0.017532     181.693333       175.948103   
-26.65888     1.0      1.000000  0.015994     158.873333       177.732050   
-26.62690     1.0      1.000000  0.020506     184.626667       172.470598   
-26.55806     1.0      1.000000  0.018555     179.343333       175.884721   
-26.54166     1.0      1.000000  0.019172     176.073333       174.644393   
-26.38592     1.0      1.000000  0.020900     183.200000       173.587014   
-26.35191     1.0      1.000000  0.018454     179.866667       174.346756   
-26.19822     1.0      1.000000  0.016515     173.070000       175.479314   
-26.11907     1.0      1.000000  0.019150     175.990000       174.294742   
-26.05133     1.0      1.000000  0.025991     197.566667       173.999257   
-26.05030     1.0      1.000000  0.020888     182.773333       173.400960   
-26.03083     1.0      1.000000  0.018791     176.023333       175.795751   
-25.96555     1.0      1.000000  0.021406     177.133333       172.387603   
-25.77476     1.0      1.000000  0.018952     166.823333       177.586252   
-25.72647     1.0      1.000000  0.020591     182.686667       173.840769   
-25.60906     1.0      0.943333  0.019056     216.066667       170.375933   
-25.56803     1.0      0.996667  0.021252     180.386667       174.608495   
-25.54907     1.0      1.000000  0.022273     190.270000       173.332603   
-25.54670     1.0      1.000000  0.022574     190.893333       175.062536   
-25.46582     1.0      1.000000  0.025165     240.903333       176.285593   
-25.36826     1.0      1.000000  0.019133     180.816667       174.642750   
-25.13323     1.0      1.000000  0.017639     180.440000       176.444869   
-25.04421     1.0      0.990000  0.019579     217.503333       175.568622   
-24.95355     1.0      1.000000  0.023126     198.916667       173.578301   
-24.94934     1.0      1.000000  0.027074     200.053333       172.249447   
-24.90026     1.0      1.000000  0.025932     190.596667       173.708830   
-24.75582     1.0      1.000000  0.019668     176.050000       174.714185   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-30.22802        0.082882             0.000000         74.233876   
-29.71144        0.085058            -5.000000         76.479214   
-29.43364        0.088166             0.000000         77.021909   
-29.37349        0.089467             0.000000         75.449759   
-28.86429        0.087389             0.000000         72.522586   
-28.18988        0.089626             0.000000         74.963496   
-28.11571        0.088813             0.000000         69.671913   
-28.07081        0.082346             0.000000         71.873984   
-27.62859        0.086674             0.000000         75.903756   
-27.52708        0.083865   

In [35]:
pop_path = "./eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/database/time_db.json"

time_res = get_exp_result(pop_path, ref_avg)


[2025.09.15 - 15:40:18] Map 1
Iteration 1: Time taken: 0.0187 seconds, Success: True
Iteration 2: Time taken: 0.0186 seconds, Success: True
Iteration 3: Time taken: 0.0186 seconds, Success: True
Iteration 4: Time taken: 0.0130 seconds, Success: True
Iteration 5: Time taken: 0.0266 seconds, Success: True
Iteration 6: Time taken: 0.0107 seconds, Success: True
Iteration 7: Time taken: 0.0165 seconds, Success: True
Iteration 8: Time taken: 0.0226 seconds, Success: True
Iteration 9: Time taken: 0.0212 seconds, Success: True
Iteration 10: Time taken: 0.0178 seconds, Success: True
Iteration 11: Time taken: 0.0176 seconds, Success: True
Iteration 12: Time taken: 0.0314 seconds, Success: True
Iteration 13: Time taken: 0.0257 seconds, Success: True
Iteration 14: Time taken: 0.0176 seconds, Success: True
Iteration 15: Time taken: 0.0245 seconds, Success: True
Iteration 16: Time taken: 0.0165 seconds, Success: True
Iteration 17: Time taken: 0.0217 seconds, Success: True
Iteration 18: Time taken: 0

In [36]:
grouped_avg = time_res.groupby('alg_name').mean()
time_res_ = pd.DataFrame(grouped_avg)
time_res_

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-36.43867     1.0      1.000000  0.022667     316.660000       174.402637   
-31.02063     1.0      0.996667  0.035073     328.723333       171.274813   
-29.79261     1.0      1.000000  0.031163     262.053333       178.022057   
-26.48735     1.0      1.000000  0.026869     338.270000       185.285031   
-25.63427     1.0      1.000000  0.030848     218.220000       179.654992   
-23.64699     1.0      1.000000  0.030989     224.786667       178.826838   
-21.85805     1.0      1.000000  0.036835     102.100000       177.960308   
-21.41658     1.0      1.000000  0.036999     110.996667       184.162923   
-17.96073     1.0      1.000000  0.055307     236.096667       171.523271   
-13.83763     1.0      1.000000  0.038324     110.936667       181.476678   
-12.53849     1.0      1.000000  0.047539     101.546667       178.516106   
-12.47480     1.0      1.000000  0.037009     255.816667       177.551463   
-12.40664     1.0      1.000000  0.037215     118.243333       183.887055   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-36.43867        0.104016             0.000000         65.311863   
-31.02063        0.086853            -0.333333         43.037449   
-29.79261        0.023196             0.000000         57.311805   
-26.48735        0.019129             0.000000         61.435519   
-25.63427        0.023746             0.000000         58.495308   
-23.64699        0.023936             0.000000         59.663340   
-21.85805        0.023726             0.000000         47.950419   
-21.41658        0.018625             0.000000         48.063274   
-17.96073        0.054316             0.000000         16.559513   
-13.83763        0.020765             0.000000         44.856714   
-12.53849        0.023651             0.000000         35.363944   
-12.47480        0.023259             0.000000         51.357746   
-12.40664        0.018616             0.000000         47.780604   

           length_improvement  smoothness_improvement  objective_score  
alg_name                                                                
-36.43867           17.699793             1803.372101        39.230295  
-31.02063           19.158453             1473.569354        30.107486  
-29.79261           16.167403              290.981409        28.348890  
-26.48735           13.307176              214.339435        27.486659  
-25.63427           15.323124              299.708222        28.241008  
-23.64699           15.757659              302.497224        28.866084  
-21.85805           16.682524              289.553030        25.842405  
-21.41658           13.928497              205.733123        23.804746  
-17.96073           19.003814              834.187811        20.541082  
-13.83763           14.970751              241.364695        23.646288  
-12.53849           16.312127              289.916199        21.846041  
-12.47480           16.301202              292.255301        26.649322  
-12.40664           14.113938              204.352482        23.824306

In [37]:
pop_path = "./eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/database/path_db.json"

path_res = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:42:41] Map 1
Iteration 1: Time taken: 0.0606 seconds, Success: True
Iteration 2: Time taken: 0.0656 seconds, Success: True
Iteration 3: Time taken: 0.0677 seconds, Success: True
Iteration 4: Time taken: 0.0576 seconds, Success: True
Iteration 5: Time taken: 0.0625 seconds, Success: True
Iteration 6: Time taken: 0.0760 seconds, Success: True
Iteration 7: Time taken: 0.0659 seconds, Success: True
Iteration 8: Time taken: 0.0892 seconds, Success: True
Iteration 9: Time taken: 0.0605 seconds, Success: True
Iteration 10: Time taken: 0.0547 seconds, Success: True
Iteration 11: Time taken: 0.0559 seconds, Success: True
Iteration 12: Time taken: 0.1055 seconds, Success: True
Iteration 13: Time taken: 0.0615 seconds, Success: True
Iteration 14: Time taken: 0.0821 seconds, Success: True
Iteration 15: Time taken: 0.0613 seconds, Success: True
Iteration 16: Time taken: 0.0610 seconds, Success: True
Iteration 17: Time taken: 0.0730 seconds, Success: True
Iteration 18: Time taken: 0

In [38]:
pop_path = "./eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/database/smoothness_db.json"

smoothness_res = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:43:23] Map 1
Iteration 1: Time taken: 0.0104 seconds, Success: True
Iteration 2: Time taken: 0.0190 seconds, Success: True
Iteration 3: Time taken: 0.0165 seconds, Success: True
Iteration 4: Time taken: 0.0170 seconds, Success: True
Iteration 5: Time taken: 0.0170 seconds, Success: True
Iteration 6: Time taken: 0.0242 seconds, Success: True
Iteration 7: Time taken: 0.0240 seconds, Success: True
Iteration 8: Time taken: 0.0172 seconds, Success: True
Iteration 9: Time taken: 0.0190 seconds, Success: True
Iteration 10: Time taken: 0.0170 seconds, Success: True
Iteration 11: Time taken: 0.0155 seconds, Success: True
Iteration 12: Time taken: 0.0231 seconds, Success: True
Iteration 13: Time taken: 0.0251 seconds, Success: True
Iteration 14: Time taken: 0.0245 seconds, Success: True
Iteration 15: Time taken: 0.0220 seconds, Success: True
Iteration 16: Time taken: 0.0137 seconds, Success: True
Iteration 17: Time taken: 0.0135 seconds, Success: True
Iteration 18: Time taken: 0

In [39]:
pop_path = "./path_planning/rag/results/pops/population_generation_9.json"

rag_res = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:46:24] Map 1
Iteration 1: Time taken: 0.0085 seconds, Success: True
Iteration 2: Time taken: 0.0095 seconds, Success: True
Iteration 3: Time taken: 0.0075 seconds, Success: True
Iteration 4: Time taken: 0.0070 seconds, Success: True
Iteration 5: Time taken: 0.0092 seconds, Success: True
Iteration 6: Time taken: 0.0062 seconds, Success: True
Iteration 7: Time taken: 0.0085 seconds, Success: True
Iteration 8: Time taken: 0.0091 seconds, Success: True
Iteration 9: Time taken: 0.0085 seconds, Success: True
Iteration 10: Time taken: 0.0095 seconds, Success: True
Iteration 11: Time taken: 0.0092 seconds, Success: True
Iteration 12: Time taken: 0.0075 seconds, Success: True
Iteration 13: Time taken: 0.0152 seconds, Success: True
Iteration 14: Time taken: 0.0211 seconds, Success: True
Iteration 15: Time taken: 0.0270 seconds, Success: True
Iteration 16: Time taken: 0.0075 seconds, Success: True
Iteration 17: Time taken: 0.0075 seconds, Success: True
Iteration 18: Time taken: 0

In [41]:
pop_path = "./paper_result/interactive_multi_agent1/results/pops/population_generation_6.json"

multi_agent_res = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:51:28] Map 1
Iteration 1: Time taken: 0.0155 seconds, Success: True
Iteration 2: Time taken: 0.0106 seconds, Success: True
Iteration 3: Time taken: 0.0074 seconds, Success: True
Iteration 4: Time taken: 0.0127 seconds, Success: True
Iteration 5: Time taken: 0.0170 seconds, Success: True
Iteration 6: Time taken: 0.0085 seconds, Success: True
Iteration 7: Time taken: 0.0140 seconds, Success: True
Iteration 8: Time taken: 0.0075 seconds, Success: True
Iteration 9: Time taken: 0.0136 seconds, Success: True
Iteration 10: Time taken: 0.0132 seconds, Success: True
Iteration 11: Time taken: 0.0115 seconds, Success: True
Iteration 12: Time taken: 0.0275 seconds, Success: True
Iteration 13: Time taken: 0.0140 seconds, Success: True
Iteration 14: Time taken: 0.0188 seconds, Success: True
Iteration 15: Time taken: 0.0190 seconds, Success: True
Iteration 16: Time taken: 0.0204 seconds, Success: True
Iteration 17: Time taken: 0.0090 seconds, Success: True
Iteration 18: Time taken: 0

In [ ]:
multi_agent_res.groupby('alg_name').mean().sort_values(by='time_improvement', ascending=False)

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-32.76205     1.0      1.000000  0.019458     234.550000       177.837095   
-34.65270     1.0      1.000000  0.020018     228.036667       176.034408   
-27.32825     1.0      1.000000  0.020513     237.680000       200.435006   
-36.21566     1.0      1.000000  0.021457     237.333333       176.291892   
-34.56709     1.0      1.000000  0.021155     234.006667       176.825118   
-40.41506     1.0      1.000000  0.022356     244.360000       177.578789   
-35.33628     1.0      1.000000  0.022417     250.350000       176.975296   
-31.39487     1.0      1.000000  0.023223     234.873333       177.600643   
-33.44837     1.0      1.000000  0.021947     213.026667       173.089965   
-33.36919     1.0      1.000000  0.027643     252.436667       175.379536   
-33.38892     1.0      1.000000  0.025892     239.396667       176.003625   
-34.94716     1.0      1.000000  0.026521     260.216667       175.278168   
-32.14549     1.0      1.000000  0.029446     264.450000       176.867350   
-27.27263     1.0      1.000000  0.026847     232.810000       179.052195   
-33.09257     1.0      1.000000  0.026183     253.466667       174.150984   
-25.95286     1.0      1.000000  0.029744     252.636667       175.572341   
-35.02465     1.0      1.000000  0.028021     258.580000       173.944240   
-32.97933     1.0      1.000000  0.032760     221.286667       178.111043   
-26.90490     1.0      1.000000  0.034011     303.973333       188.054460   
-26.69522     1.0      0.976667  0.029802     214.570000       178.670610   
-27.43438     1.0      1.000000  0.034824     240.180000       181.505143   
-28.69397     1.0      1.000000  0.029904     254.720000       173.924960   
-35.41092     1.0      0.996667  0.033305     289.286667       177.026334   
-29.68817     1.0      0.996667  0.032441     288.300000       176.598652   
-25.23044     1.0      1.000000  0.036081     232.236667       177.139482   
-31.33248     1.0      1.000000  0.037668     237.110000       176.030512   
-28.68700     1.0      0.986667  0.036773     204.016667       178.096397   
-24.99390     1.0      0.990000  0.041471     229.276667       179.511582   
-27.40187     1.0      1.000000  0.044569     262.053333       175.695441   
-27.74825     1.0      1.000000  0.046502     212.883333       176.011510   
-27.59476     1.0      1.000000  0.045678     266.766667       177.001982   
-28.23296     1.0      1.000000  0.044168     277.060000       176.999687   
-26.08123     1.0      1.000000  0.054489     236.720000       176.246206   
-28.40282     1.0      1.000000  0.061858     240.190000       175.837585   
-26.44459     1.0      1.000000  0.065710     237.670000       175.903525   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-32.76205        0.070721             0.000000         73.141724   
-34.65270        0.084219             0.000000         72.898009   
-27.32825        0.014415             0.000000         71.931681   
-36.21566        0.082764             0.000000         71.232225   
-34.56709        0.081777             0.000000         70.511386   
-40.41506        0.081882             0.000000         69.977829   
-35.33628        0.084052             0.000000         69.926910   
-31.39487        0.084197             0.000000         69.642060   
-33.44837        0.065925             0.000000         69.132005   
-33.36919        0.082800             0.000000         65.762984   
-33.38892        0.081422             0.000000         65.403546   
-34.94716        0.085552             0.000000         63.140460   
-32.14549        0.076688             0.000000         62.620127   
-27.27263        0.023650             0.000000         62.465633   
-33.09257        0.080056             0.000000         62.284472   
-25.9

In [ ]:
rag_res.groupby('alg_name').mean().sort_values(by='objective_score', ascending=False)

In [43]:
pop_path = "./paper_result/interactive_multi_agent2/results/pops/population_generation_10.json"

ima_res2 = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 15:57:22] Map 1
Iteration 1: Time taken: 0.0130 seconds, Success: True
Iteration 2: Time taken: 0.0337 seconds, Success: True
Iteration 3: Time taken: 0.0105 seconds, Success: True
Iteration 4: Time taken: 0.0212 seconds, Success: True
Iteration 5: Time taken: 0.0070 seconds, Success: True
Iteration 6: Time taken: 0.0075 seconds, Success: True
Iteration 7: Time taken: 0.0085 seconds, Success: True
Iteration 8: Time taken: 0.0155 seconds, Success: True
Iteration 9: Time taken: 0.0065 seconds, Success: True
Iteration 10: Time taken: 0.0095 seconds, Success: True
Iteration 11: Time taken: 0.0075 seconds, Success: True
Iteration 12: Time taken: 0.0100 seconds, Success: True
Iteration 13: Time taken: 0.0315 seconds, Success: True
Iteration 14: Time taken: 0.0105 seconds, Success: True
Iteration 15: Time taken: 0.0135 seconds, Success: True
Iteration 16: Time taken: 0.0061 seconds, Success: True
Iteration 17: Time taken: 0.0083 seconds, Success: True
Iteration 18: Time taken: 0

In [44]:
ima_res2.groupby('alg_name').mean().sort_values(by='length_improvement', ascending=False)

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-37.37284     1.0           1.0  0.022448     222.823333       171.802445   
-38.54314     1.0           1.0  0.018978     201.826667       172.328341   
-38.01395     1.0           1.0  0.019600     209.756667       172.449503   
-35.05016     1.0           1.0  0.021248     210.623333       172.204986   
-38.53073     1.0           1.0  0.020221     207.730000       172.661390   
-34.18597     1.0           1.0  0.022155     182.093333       172.422268   
-35.51213     1.0           1.0  0.020375     210.430000       173.089159   
-39.02046     1.0           1.0  0.018404     198.183333       173.003572   
-31.40894     1.0           1.0  0.028373     208.520000       173.024828   
-36.21283     1.0           1.0  0.022030     174.113333       172.786613   
-32.08129     1.0           1.0  0.021499     221.450000       173.228831   
-35.47883     1.0           1.0  0.019330     208.053333       173.409424   
-35.65902     1.0           1.0  0.019470     204.806667       173.492348   
-34.76108     1.0           1.0  0.024883     199.006667       173.010644   
-32.77140     1.0           1.0  0.032289     191.386667       173.163225   
-34.19888     1.0           1.0  0.023408     230.653333       173.541009   
-28.94013     1.0           1.0  0.029792     240.906667       173.814935   
-35.99817     1.0           1.0  0.022281     182.713333       173.386955   
-32.05464     1.0           1.0  0.020888     185.560000       173.486266   
-33.58444     1.0           1.0  0.031784     195.086667       173.934280   
-33.90720     1.0           1.0  0.023020     240.853333       174.476217   
-32.74393     1.0           1.0  0.031770     182.753333       174.387547   
-33.51759     1.0           1.0  0.017001     185.146667       174.556705   
-37.67647     1.0           1.0  0.022677     238.176667       174.970997   
-29.96541     1.0           1.0  0.039351     228.106667       175.673022   
-29.86995     1.0           1.0  0.035878     588.720000       175.828574   
-32.13033     1.0           1.0  0.036843     589.160000       176.154831   
-30.37323     1.0           1.0  0.037977     276.156667       175.874186   
-28.63426     1.0           1.0  0.037026     285.893333       175.813374   
-37.13607     1.0           1.0  0.029262     277.876667       175.982412   
-29.65900     1.0           1.0  0.033373     241.923333       176.877428   
-34.24624     1.0           1.0  0.015953     204.916667       177.675169   
-31.80647     1.0           1.0  0.028507     236.600000       177.485765   
-31.88223     1.0           1.0  0.019093     203.766667       177.928738   
-32.71539     1.0           1.0  0.028773     199.893333       177.285174   
-30.11247     1.0           1.0  0.030450     231.896667       177.364223   
-32.98846     1.0           1.0  0.029702     234.320000       177.928593   
-36.65222     1.0           1.0  0.020893     183.460000       178.594818   
-34.04928     1.0           1.0  0.019021     167.130000       180.297996   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-37.37284        0.085170                  0.0         68.001380   
-38.54314        0.098121                  0.0         74.738821   
-38.01395        0.098464                  0.0         75.174333   
-35.05016        0.084201                  0.0         69.010893   
-38.53073        0.098234                  0.0         73.651055   
-34.18597        0.081586                  0.0         68.709085   
-35.51213        0.096888                  0.0         72.699402   
-39.02046        0.095850                  0.0         74.961169   
-31.40894        0.086261                  0.0         57.403158   
-36.21283        0.079850                  0.0         68.702232   
-32.08129        0.089557            

In [45]:
pop_path = "./paper_result/interactive_multi_agent3/results/pops/population_generation_15.json"

ima_res3 = get_exp_result(pop_path, ref_avg)

[2025.09.15 - 16:02:28] Map 1
Iteration 1: Time taken: 0.0180 seconds, Success: True
Iteration 2: Time taken: 0.0180 seconds, Success: True
Iteration 3: Time taken: 0.0187 seconds, Success: True
Iteration 4: Time taken: 0.0130 seconds, Success: True
Iteration 5: Time taken: 0.0250 seconds, Success: True
Iteration 6: Time taken: 0.0124 seconds, Success: True
Iteration 7: Time taken: 0.0171 seconds, Success: True
Iteration 8: Time taken: 0.0235 seconds, Success: True
Iteration 9: Time taken: 0.0210 seconds, Success: True
Iteration 10: Time taken: 0.0178 seconds, Success: True
Iteration 11: Time taken: 0.0165 seconds, Success: True
Iteration 12: Time taken: 0.0320 seconds, Success: True
Iteration 13: Time taken: 0.0251 seconds, Success: True
Iteration 14: Time taken: 0.0051 seconds, Success: True
Iteration 15: Time taken: 0.0372 seconds, Success: True
Iteration 16: Time taken: 0.0150 seconds, Success: True
Iteration 17: Time taken: 0.0231 seconds, Success: True
Iteration 18: Time taken: 0

In [46]:
ima_res3.groupby('alg_name').mean().sort_values(by='length_improvement', ascending=False)

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-31.02063     1.0           1.0  0.034018     333.410000       170.149248   
-36.26177     1.0           1.0  0.017157     225.100000       174.043268   
-36.43867     1.0           1.0  0.022340     316.660000       174.402637   
-34.89579     1.0           1.0  0.024476     251.136667       174.262257   
-29.79261     1.0           1.0  0.029905     257.316667       177.462747   
-25.63427     1.0           1.0  0.034243     233.656667       179.335229   
-29.41149     1.0           1.0  0.023137     223.993333       179.947195   
-26.48735     1.0           1.0  0.029994     352.343333       185.303368   
-25.59587     1.0           1.0  0.036850     255.966667       185.402809   
-24.61754     1.0           1.0  0.020959     232.906667       188.533670   
-24.71377     1.0           1.0  0.018479     224.263333       197.140246   
-24.61746     1.0           1.0  0.008266     188.046667       218.174524   
-25.31044     1.0           1.0  0.009933     218.420000       218.929756   
-23.99146     1.0           1.0  0.013296     229.936667       218.989623   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-31.02063        0.080548                  0.0         44.430501   
-36.26177        0.093743                  0.0         74.613517   
-36.43867        0.104016                  0.0         65.854303   
-34.89579        0.099261                  0.0         66.852133   
-29.79261        0.023347                  0.0         59.387620   
-25.63427        0.023707                  0.0         53.977241   
-29.41149        0.021662                  0.0         68.018695   
-26.48735        0.019097                  0.0         57.012949   
-25.59587        0.015865                  0.0         52.825999   
-24.61754        0.018725                  0.0         71.514145   
-24.71377        0.014876                  0.0         75.293585   
-24.61746        0.010068                  0.0         89.642932   
-25.31044        0.010062                  0.0         87.922024   
-23.99146        0.009976                  0.0         83.266802   

           length_improvement  smoothness_improvement  objective_score  
alg_name                                                                
-31.02063           19.844291             1380.220752        32.136829  
-36.26177           17.904699             1610.966060        41.181705  
-36.43867           17.699793             1803.372101        39.393027  
-34.89579           17.646213             1725.425216        39.270494  
-29.79261           16.536560              292.552724        29.200986  
-25.63427           15.526284              298.859134        27.003238  
-29.41149           15.167825              264.565230        30.829130  
-26.48735           13.342917              213.432814        26.176799  
-25.59587           13.081325              165.715396        24.525172  
-24.61754           11.475881              210.638089        29.392963  
-24.71377            7.707919              145.820608        27.941930  
-24.61746           -2.398030               68.592457        25.797024  
-25.31044           -2.881282               68.733542        24.991506  
-23.99146           -2.937903               67.359822        23.554098

In [95]:
pop_path = "./paper_result/interactive_multi_agent5/results/pops/population_generation_23.json"

ima_res5 = get_exp_result(pop_path, ref_avg)
ima_res5.groupby('alg_name').mean().sort_values(by='length_improvement', ascending=False)

[2025.09.17 - 10:52:21] Map 1
Iteration 1: Time taken: 0.0113 seconds, Success: True
Iteration 2: Time taken: 0.0383 seconds, Success: True
Iteration 3: Time taken: 0.0130 seconds, Success: True
Iteration 4: Time taken: 0.0187 seconds, Success: True
Iteration 5: Time taken: 0.0122 seconds, Success: True
Iteration 6: Time taken: 0.0088 seconds, Success: True
Iteration 7: Time taken: 0.0201 seconds, Success: True
Iteration 8: Time taken: 0.0114 seconds, Success: True
Iteration 9: Time taken: 0.0136 seconds, Success: True
Iteration 10: Time taken: 0.0184 seconds, Success: True
Iteration 11: Time taken: 0.0209 seconds, Success: True
Iteration 12: Time taken: 0.0049 seconds, Success: True
Iteration 13: Time taken: 0.0173 seconds, Success: True
Iteration 14: Time taken: 0.0154 seconds, Success: True
Iteration 15: Time taken: 0.0144 seconds, Success: True
Iteration 16: Time taken: 0.0193 seconds, Success: True
Iteration 17: Time taken: 0.0559 seconds, Success: True
Iteration 18: Time taken: 0

map_id  success_rate  time_avg  num_nodes_avg  path_length_avg  \
alg_name                                                                    
-35.35386     1.0      0.996667  0.032297     247.393333       172.984592   
-34.77469     1.0      1.000000  0.026004     200.010000       173.624689   
-32.09066     1.0      1.000000  0.033658     199.613333       174.115880   
-32.90290     1.0      1.000000  0.027069     203.043333       174.259721   
-37.48589     1.0      1.000000  0.021655     182.300000       173.924949   
-33.48325     1.0      0.973333  0.026284     208.456667       174.418548   
-31.48243     1.0      1.000000  0.032388     193.080000       174.468061   
-33.40298     1.0      1.000000  0.041057     208.300000       175.193576   
-33.96721     1.0      1.000000  0.026031     173.760000       175.103927   
-34.03393     1.0      1.000000  0.027221     200.633333       175.565540   
-31.70156     1.0      0.996667  0.025276     195.200000       176.236320   
-33.94541     1.0      1.000000  0.024658     153.643333       176.310665   
-31.43162     1.0      1.000000  0.026771     183.200000       176.895139   
-34.45401     1.0      1.000000  0.021493     173.653333       177.229223   
-30.76555     1.0      1.000000  0.028141     242.363333       178.420373   
-31.91279     1.0      0.996667  0.027383     202.270000       182.808726   

           smoothness_avg  success_improvement  time_improvement  \
alg_name                                                           
-35.35386        0.091745            -0.333333         56.325005   
-34.77469        0.088777             0.000000         62.075643   
-32.09066        0.089771             0.000000         57.113024   
-32.90290        0.086706             0.000000         61.164470   
-37.48589        0.100829             0.000000         67.132913   
-33.48325        0.089346            -2.666667         58.092086   
-31.48243        0.090022             0.000000         52.584199   
-33.40298        0.086101             0.000000         46.037723   
-33.96721        0.103360             0.000000         60.035416   
-34.03393        0.091021             0.000000         60.233769   
-31.70156        0.091222            -0.333333         61.534250   
-33.94541        0.099007             0.000000         61.609016   
-31.43162        0.093753             0.000000         57.940762   
-34.45401        0.090921             0.000000         67.479154   
-30.76555        0.090402             0.000000         58.707392   
-31.91279        0.092243            -0.333333         61.680721   

           length_improvement  smoothness_improvement  objective_score  
alg_name                                                                
-35.35386           18.632901             1553.086224        34.176007  
-34.77469           18.186651             1519.528448        37.132326  
-32.09066           18.075255             1561.978449        35.788952  
-32.90290           18.066229             1497.768941        36.677923  
-37.48589           17.928012             1733.114913        39.562255  
-33.48325           17.872076             1550.726134        22.571168  
-31.48243           17.814423             1535.976944        34.143798  
-33.40298           17.498143             1466.917397        31.644790  
-33.96721           17.423761             1804.544178        37.487602  
-34.03393           17.302788             1570.909439        36.306351  
-31.70156           16.880220             1559.938414        34.721432  
-33.94541           16.802157             1701.657629        37.072287  
-31.43162           16.579091             1614.178942        35.400578  
-34.45401           16.441380             1572.937710        37.973263  
-30.76555           15.642321             1528.260326        34.638912  
-31.91279           13.568842             1576.812217        32.862916

In [ ]:
pop_path = "./paper_result/interactive_multi_agent2/results/pops/db/path_db.json"

ima_pathdb = get_exp_result(pop_path, ref_avg)

In [ ]:
ima_pathdb.groupby('alg_name').mean().sort_values(by='length_improvement', ascending=False)

In [ ]:
total_df['cls_try'] = 0 # classic method
res1['cls_try'] = 1 # expert1
res2['cls_try'] = 2 # expert2
res3['cls_try'] = 3 # eoh1
res4['cls_try'] = 4 # expert_analysis1
time_res['cls_try'] = 5 # time_expert_db
path_res['cls_try'] = 6 # path_expert_db
smoothness_res['cls_try'] = 7 # smoothness_expert_db

code2label = {
    0: "classic",
    1: "expert1",
    2: "expert2",
    3: "eoh1",
    4: "expert_analysis1",
    5: "time_expert_db",
    6: "path_expert_db",
    7: "smoothness_expert_db",
}


In [ ]:
def get_avg_result(df, clas_name, success_drop=False):
    # alg_name 기준으로 groupby하여 평균값 계산
    grouped_avg = df.groupby('alg_name').mean()
    total_statics = pd.DataFrame(grouped_avg)
    total_statics = total_statics.drop(["map_id"], axis=1)
    total_statics = total_statics.sort_values(by='objective_score', ascending=False)
    total_statics['cls_try'] = clas_name
    # total_statics = total_statics.sort_values(by='time_improvement', ascending=False)

    if success_drop:
        total_statics = total_statics[total_statics['success_rate'] >= 1]
    
    return total_statics

In [ ]:
result_list = [total_df, res1, res2, res3, res4, time_res, path_res, smoothness_res]

In [ ]:
whole_res_list = list()
for i, res in enumerate(result_list):
    whole_res_list.append(get_avg_result(res, code2label[i], True if not i==0 else False))

In [ ]:
whole_res_list[3].round(3

In [ ]:
whole_df[whole_df['cls_try'].isin(['expert_analysis1'])].sort_values(by='objective_score', ascending=False)

In [ ]:
whole_df = pd.concat(whole_res_list, axis=0)
whole_df = whole_df.sort_values(by='objective_score', ascending=False)
# whole_df = whole_df.sort_values(by='time_improvement', ascending=False)
whole_df[:20]

In [ ]:
whole_df = whole_df.sort_values(by='time_improvement', ascending=False)
whole_df[:20]

In [ ]:
col_map = {
    # "map_id": "Map ID",
    "success_rate": "성공률 (Success Rate)",
    "time_avg": "평균 시간 (Time Avg)",
    # "num_nodes_avg": "평균 노드 수 (Num Nodes Avg)",
    "path_length_avg": "평균 경로 길이 (Path Length Avg)",
    "success_improvement": "성공률 개선 (Success Improvement)",
    "time_improvement": "시간 개선 (%)",
    "length_improvement": "경로 개선 (%)",
    "objective_score": "종합 점수 (Objective Score)"
}

df_pretty = grouped_avg.rename(columns=col_map)
df_pretty = df_pretty.round(3)
df_pretty = df_pretty.sort_values("종합 점수 (Objective Score)", ascending=False)
display(df_pretty)

In [ ]:
import json, os

In [ ]:
def reset_obj_score(method):
    maps = [multi_obs_map, maze_map, narrow_map]
    benchmarker = MultiMapBenchmarker(maps=maps, iter=10)

    g_total_df = pd.DataFrame()

    code_string = method['code']
    namedf = pd.DataFrame()
    namedf['alg_name'] = [method['objective']]* len(maps)
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        planning_module = types.ModuleType("planning_module")
        exec(import_string+code_string, planning_module.__dict__)
        sys.modules[planning_module.__name__] = planning_module
        try:
            planner = planning_module.Planner(max_iter=5000)
        except:
            pass
        res, avg_rest = benchmarker.run(planner.plan)
        
        if avg_rest is None: return 9999
        imp_res = MultiMapBenchmarker.get_improvement(ref_avg, avg_rest)

        # res_df = pd.concat([namedf, avg_rest, imp_res], axis=1)
        # g_total_df = pd.concat([g_total_df, res_df], axis=0)

        return -imp_res['objective_score'].mean()

def get_best_pop(path):
    alg_save = []

    for i in range(1,11):
        pop_path = f"{path}/population_generation_{i}.json"
        tmp_alg = []
        if os.path.exists(pop_path):
            with open(pop_path, "r") as f:
                data = json.load(f)
                tmp_alg = sorted(
                [alg for alg in data if alg.get('operator') != 'initial'],
                key=lambda x: x.get('objective', float('inf'))
                )
            new_tmp_alg = []
            for i, alg in enumerate(tmp_alg[:10]):
                tmp_alg[i]['objective'] = reset_obj_score(alg)
                new_tmp_alg.append(tmp_alg[i])
                
            new_tmp_alg = sorted(
                [alg for alg in data if alg.get('operator') != 'initial'],
                key=lambda x: x.get('objective', float('inf')))
            
            alg_save.append(new_tmp_alg[0])

    return alg_save
        

In [ ]:
pop_path = "./path_planning/mobj1/results/pops"
expert1 = get_best_pop(pop_path)

In [ ]:
pop_path = "./path_planning/basic_eoh/results/pops"
basic = get_best_pop(pop_path)

In [ ]:
pop_path = "./path_planning/mobj_analysis/results/pops"
analysis = get_best_pop(pop_path)

In [ ]:
pop_path = "./path_planning/rag/results/pops"
rag = get_best_pop(pop_path)

In [ ]:
def enforce_non_decreasing(arr):
    if not arr:
        return []

    result = [arr[0]]  # 첫 번째 값은 그대로
    for i in range(1, len(arr)):
        if arr[i]['objective'] > result[-1]['objective']:
            result.append(result[-1])   # 이전 값 유지
        else:
            result.append(arr[i])       # 현재 값 유지
    return result

In [ ]:
alg_list1 = [basic, expert1, analysis, rag]

In [ ]:
[alg['objective'] for alg in alg_list1[1]]

In [ ]:
basic, expert1, analysis, rag = enforce_non_decreasing(basic), enforce_non_decreasing(expert1), enforce_non_decreasing(analysis), enforce_non_decreasing(rag)

alg_list = [basic, expert1, analysis, rag]

In [ ]:
analysis

In [ ]:
import plotly.express as px
import pandas as pd
import plotly.graph_objects as go


In [ ]:
print(["bottom center"]+["top center"]*7+["bottom center"]*2)

In [ ]:
fig = go.Figure()

name = ['EoH', 'Expert DB(Ours)', 'Expert+Analysis DB(Ours)', 'RAG']
p_list = []
p_list.append(["top center"]+["bottom center"]+["top center"]*8)
p_list.append(["bottom center"]+["top center"]*9)
p_list.append(["bottom center"]+["top center"]*7+["bottom center"]*2)
p_list.append(["bottom center"]+["top center"]*7+["bottom center"]*2)

for i, alg in enumerate(alg_list):
    fig.add_trace(go.Scatter(
        x=[i+1 for i in range(len(alg))],
        y=[-x['objective'] for x in alg],
        mode="lines+markers+text",
        text=["{:.2f}".format(-x['objective']) for x in alg],           # 표시할 텍스트 값
        textposition=p_list[i],
        name=name[i],
        hovertemplate="Step: %{x}<br>Objective: %{y}<br>Operator: {}"
    ))

fig.update_layout(
    width=800,    # 가로 크기 (px)
    height=500,   # 세로 크기 (px)
)


# 레이아웃
fig.update_layout(
    # title="Objective over Number of Generations",
    xaxis_title="Number of generations",
    yaxis_title="Objective",
    template="plotly_white",
    legend_title="Method"
)
fig.update_layout(
    legend=dict(
        x=0.65,   # 가로 위치 (0=왼쪽, 1=오른쪽)
        y=0.1,  # 세로 위치 (0=아래, 1=위)
        bgcolor="rgba(255,255,255,0.7)",  # 배경 색상 (투명도 조절)
        bordercolor="black",              # 테두리 색상
        borderwidth=1
    )
)
fig.update_layout(
    xaxis=dict(
        showline=True,          # 축 라인 표시
        linewidth=2,            # 축 라인 두께
        linecolor="black",      # 축 라인 색
        showgrid=True,          # 그리드 표시 여부
        gridcolor="lightgray",  # 그리드 색상
        tickmode="linear",      # 눈금 방식 (linear / array / auto)
        dtick=1,                # 눈금 간격 (예: 1씩 증가)
        tickangle=0,            # 눈금 글자 각도
        tickfont=dict(size=12)  # 눈금 글자 크기
    )
)
fig.update_layout(
    yaxis=dict(
        showline=True,          # 축 라인 표시
        linewidth=2,            # 축 라인 두께
        linecolor="black",      # 축 라인 색
        showgrid=True,          # 그리드 표시 여부
        gridcolor="lightgray",  # 그리드 색상
        tickmode="linear",      # 눈금 방식 (linear / array / auto)
        dtick=5,                # 눈금 간격 (예: 1씩 증가)
        tickangle=0,            # 눈금 글자 각도
        tickfont=dict(size=12)  # 눈금 글자 크기
    )
)
fig.show()

### LM TEST

In [ ]:
from eoh.llm.interface_LLM import InterfaceLLM
from eoh.utils.getParas import Paras
from eoh.methods.eoh.eoh_evolution import Evolution
from eoh.problems.optimization.classic_benchmark_path_planning.utils.prompts import GetPrompts
import re
paras = Paras()

In [ ]:
ee = Evolution("api.openai.com", api_key, "gpt-4.1-mini-2025-04-14", False, None, True, GetPrompts())
illm = InterfaceLLM("api.openai.com", api_key, "gpt-4.1-mini-2025-04-14", False, None, True)

In [ ]:
pc = ee.get_prompt([result_data[3]], 'e1')

In [ ]:
gcode = illm.get_response(pc)

In [ ]:
print(gcode)

In [ ]:
c, m, a = ee._extract_alg(gcode)

In [ ]:
response = ee.get_analysis(classic_method[0]['code'], classic_method[5]['code'], 'time')

In [ ]:
classic_method[0]

In [ ]:
print(response)

In [ ]:
print( "Traceback (most recent call last):\n  File \"c:\\workspace\\eoh_path_planning\\eoh\\src\\eoh\\problems\\optimization\\classic_benchmark_path_planning\\run.py\", line 96, in evaluate\n    exec(self.import_string+code_string, planning_module.__dict__)\nTypeError: can only concatenate str (not \"NoneType\") to str\n")

In [ ]:
time.strftime('%Y/%m/%d - %H:%M:%S')

In [ ]:
random.randint(0, 1)


In [ ]:
import random

In [ ]:
inv = 163.66

(986.327 - inv) / 986.327

## RAG Test

In [48]:
from langchain_openai import OpenAIEmbeddings
from langchain_chroma import Chroma
from langchain_community.document_loaders import JSONLoader
# Initialize with an embedding model
embeddings = OpenAIEmbeddings(api_key=api_key,
                              model="text-embedding-3-small")
vector_store = Chroma(embedding_function=embeddings)

In [49]:
# Load a json file
loader = JSONLoader(
    file_path="./eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/database/smoothness_analysis_db.json",
    jq_schema=".[].analysis",  # This extracts the content field from each array item
    text_content=True
)
documents = loader.load()
print(documents)

[Document(metadata={'source': 'C:\\Workspace\\EoH_Path_planning\\eoh\\src\\eoh\\problems\\optimization\\classic_benchmark_path_planning\\utils\\database\\smoothness_analysis_db.json', 'seq_num': 1}, page_content='1. Problem of the parents algorithm:\n   - Linear nearest neighbor searches without spatial data structures cause inefficient scaling and longer planning times.\n   - Fixed or non-adaptive neighbor radius limits optimal rewiring and path quality improvements.\n   - Lack of alternating tree growth and balanced exploration between start and goal trees.\n   - Absence of goal biasing in sampling reduces focused exploration towards the goal.\n   - No logarithmically shrinking neighbor radius to balance exploration and convergence, limiting path smoothness.\n   - Insufficient rewiring mechanism and naive edge handling lead to jagged paths and inefficient path shortening.\n\n2. Primary contributors to the performance improvement:\n   - Implementation of alternating bidirectional tree

In [50]:
from langchain_community.vectorstores import FAISS


In [51]:
vector_db = FAISS.from_documents(documents, embeddings)

In [52]:
isinstance(vector_db, FAISS)

True

In [86]:
# For query transformation
from langchain.prompts import PromptTemplate
from langchain_openai import ChatOpenAI
from langchain_core.output_parsers import StrOutputParser

# For basic RAG implementation
from langchain_community.document_loaders import JSONLoader
from langchain_openai import OpenAIEmbeddings
from langchain_community.vectorstores import FAISS

def metadata_func(record: dict, metadata: dict) -> dict:
    return {"sol": record.get("sol", "")}

# 1. Load documents
loader = JSONLoader(
    file_path="./eoh/src/eoh/problems/optimization/classic_benchmark_path_planning/utils/database/smoothness_analysis_db_test.json",
    jq_schema=".[].analysis",  # This extracts the content field from each array item
    content_key="prob",
    metadata_func=metadata_func,
    text_content=False
)
documents = loader.load()

# 2. Convert to vectors
embedder = OpenAIEmbeddings(api_key=api_key,
                              model="text-embedding-3-small")
embeddings = embedder.embed_documents([doc.page_content for doc in documents])

# 3. Store in vector database
vector_db = FAISS.from_documents(documents, embedder)

# 4. Retrieve similar docs
query = "What are the effects of climate change?"
results = vector_db.similarity_search(query=query, k=3)
results_with_score = vector_db.similarity_search_with_score(query=query, k=3)

In [90]:
results[0].page_content

'ejfioejawfdopnsaoifsa'

In [73]:
results_with_score[0][0]

Document(id='66bb2e21-143e-4a49-8a3e-aa69e4d16b2d', metadata={'source': 'C:\\Workspace\\EoH_Path_planning\\eoh\\src\\eoh\\problems\\optimization\\classic_benchmark_path_planning\\utils\\database\\smoothness_analysis_db.json', 'seq_num': 10}, page_content='1. Problem of the parents algorithm:\n   - Inefficient and repetitive recursive cost updates caused computational overhead and slowed planning time.\n   - Linear nearest and near neighbor searches without spatial indexing limited scalability as tree size increased.\n   - Fixed large rewiring radius and inconsistent parent-child edge management led to inflated path length and suboptimal smoothness.\n   - Lack of explicit smoothing or curvature consideration during rewiring resulted in piecewise linear paths with sharp turns.\n\n2. Primary contributors to the performance improvement:\n   - More consistent parent-child edge updates including proper child removal, reducing redundancy and enabling efficient cost propagation.\n   - Increase

In [93]:
results_with_score[0][0].metadata

{'sol': '1. Problem of the parents algorithm:\n   - Linear nearest neighbor searches without spatial data structures cause inefficient scaling and longer planning times.\n   - Fixed or non-adaptive neighbor radius limits optimal rewiring and path quality improvements.\n   - Lack of alternating tree growth and balanced exploration between start and goal trees.\n   - Absence of goal biasing in sampling reduces focused exploration towards the goal.\n   - No logarithmically shrinking neighbor radius to balance exploration and convergence, limiting path smoothness.\n   - Insufficient rewiring mechanism and naive edge handling lead to jagged paths and inefficient path shortening.\n\n2. Primary contributors to the performance improvement:\n   - Implementation of alternating bidirectional tree expansions to balance growth and accelerate connection.\n   - Incorporation of goal biasing in sampling to improve convergence towards the goal.\n   - Use of a logarithmically shrinking neighbor radius e

In [ ]:
results[0].page_content

In [ ]:
import http
import json

In [ ]:
prompt_content = 'hi?'
api_endpoint = "api.openai.com"
model_LLM = "gpt-4.1-mini-2025-04-14"

payload_explanation = json.dumps(
    {
        "model": model_LLM,
        "messages": [
            # {"role": "system", "content": "You are a helpful assistant."},
            {"role": "user", "content": prompt_content},
            {"role": "user", "content": "analyze the wheather"},
            # {"role": "user", "content": prompt_content}
            
        ],
    }
)

headers = {
                "Authorization": "Bearer " + api_key,
                "User-Agent": "Apifox/1.0.0 (https://apifox.com)",
                "Content-Type": "application/json",
                "x-api2d-no-cache": 1,
            }

conn = http.client.HTTPSConnection(api_endpoint)
conn.request("POST", "/v1/chat/completions", payload_explanation, headers)

res = conn.getresponse()

In [ ]:
data = res.read()

In [ ]:
map

In [ ]:
data

In [ ]:
json_data = json.loads(data)

In [ ]:
json_data

In [ ]:
print('OUTPUT CONTRACT:\n- Adaptive Bi-Directional Informed Sampling Tree with Dynamic Radius and Progressive Path Smoothing\n- The planner simultaneously grows two trees from start and goal nodes using adaptive sampling focused within an informed ellipsoid, dynamically adjusting neighbor connection radius, incrementally connecting and rewiring nodes, and progressively smoothing the path during search to efficiently converge on shorter, smoother, and more robust trajectories.\n\n```python\nclass Node:\n    def __init__(self, position, parent=None, cost=0.0):\n        self.position = position\n        self.parent = parent\n        self.cost = cost\n        self.children = []\n        self.valid = True\n\n    def add_child(self, child_node):\n        self.children.append(child_node)\n        child_node.parent = self\n\n    def remove_child(self, child_node):\n        if child_node in self.children:\n            self.children.remove(child_node)\n            child_node.parent = None\n\n    def update_parent(self, new_parent, new_cost):\n        if self.parent:\n            self.parent.remove_child(self)\n        self.parent = new_parent\n        self.cost = new_cost\n        new_parent.add_child(self)\n        self._update_descendants_costs()\n\n    def _update_descendants_costs(self):\n        nodes_to_update = list(self.children)\n        while nodes_to_update:\n            current = nodes_to_update.pop()\n            if current.parent:\n                dist = self._distance(current.parent.position, current.position)\n                current.cost = current.parent.cost + dist\n                nodes_to_update.extend(current.children)\n\n    @staticmethod\n    def _distance(a, b):\n        import math\n        return math.dist(a, b)\n\n    def path_from_root(self):\n        path, node = [], self\n        while node:\n            path.append(node.position)\n            node = node.parent\n        return path[::-1]\n\n\nclass Planner:\n    def __init__(self, max_iter=5000, base_step=5.0, max_rewire_radius=25.0, min_rewire_radius=5.0, goal_sample_rate=0.1):\n        self.max_iter = max_iter\n        self.base_step = base_step\n        self.max_rewire_radius = max_rewire_radius\n        self.min_rewire_radius = min_rewire_radius\n        self.goal_sample_rate = goal_sample_rate\n\n    def plan(self, map) -> \'PlannerResult\':\n        import time\n        import math\n        import random\n\n        start_time = time.monotonic()\n        time_limit = 30.0\n\n        bounds = map.size\n        start_pos = map.start\n        goal_pos = map.goal\n        obstacles = map.obstacles\n        is_3d = len(bounds) == 3\n        dim = len(bounds)\n\n        tree_start = [Node(start_pos)]\n        tree_goal = [Node(goal_pos)]\n        nodes = [tree_start[0], tree_goal[0]]\n        edges = []\n        success = False\n        best_path = []\n        c_min = math.dist(start_pos, goal_pos)\n        c_best = float("inf")\n\n        def adaptive_radius(node_count):\n            from math import log, pow\n            gamma_rrt_star = self.max_rewire_radius\n            r = gamma_rrt_star * pow((math.log(node_count + 1) / (node_count + 1)), 1 / dim)\n            return max(self.min_rewire_radius, min(r, self.max_rewire_radius))\n\n        def informed_sample():\n            if c_best == float("inf"):\n                # Uniform random sample\n                return tuple(random.uniform(0, bounds[d]) for d in range(dim))\n            # Ellipsoidal informed sampling\n            import numpy as np\n            c = c_best\n            center = np.array([(s + g) / 2 for s, g in zip(start_pos, goal_pos)])\n            a1 = np.array(goal_pos) - np.array(start_pos)\n            if np.linalg.norm(a1) == 0:\n                return tuple(center)\n            e = a1 / np.linalg.norm(a1)\n            I = np.eye(dim)\n            M = np.outer(e, I[0])\n            U, _, Vt = np.linalg.svd(M)\n            det_val = np.linalg.det(U) * np.linalg.det(Vt)\n            C = U @ np.diag([1] * (dim - 1) + [det_val]) @ Vt\n            r1 = c / 2.0\n            r2 = math.sqrt(c ** 2 - c_min ** 2) / 2.0\n            L = np.diag([r1] + [r2] * (dim - 1))\n            while True:\n                x_ball = np.random.normal(0, 1, dim)\n                x_ball = x_ball / np.linalg.norm(x_ball)  # unit vector\n                scale = random.random() ** (1 / dim)\n                x_ball = x_ball * scale\n                x_rand = C @ L @ x_ball + center\n                if all(0 <= x_rand[d] <= bounds[d] for d in range(dim)):\n                    sample_point = tuple(x_rand)\n                    if not self._is_in_obstacle(sample_point, obstacles, is_3d):\n                        return sample_point\n\n        def steer(from_pos, to_pos, step):\n            dist = math.dist(from_pos, to_pos)\n            if dist <= step:\n                return to_pos\n            ratio = step / dist\n            return tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * ratio for d in range(len(from_pos)))\n\n        def collision_free_edge(from_pos, to_pos):\n            # smaller resolution for better accuracy near obstacles\n            resolution = self.base_step * 0.25\n            return not self._is_edge_in_obstacle(from_pos, to_pos, obstacles, is_3d, resolution)\n\n        def try_connect_trees(node_new, tree_other, nodes, edges):\n            # Incremental connect attempt with rewiring\n            curr = node_new\n            while True:\n                nearest_other = min(tree_other, key=lambda n: math.dist(n.position, curr.position))\n                dist = math.dist(curr.position, nearest_other.position)\n                if dist <= self.base_step:\n                    if collision_free_edge(curr.position, nearest_other.position):\n                        # connect\n                        if nearest_other.parent is None:\n                            nearest_other.parent = curr\n                            nearest_other.cost = curr.cost + dist\n                            curr.add_child(nearest_other)\n                            edges.append((curr, nearest_other))\n                        else:\n                            # rewiring if better cost\n                            if nearest_other.cost > curr.cost + dist:\n                                nearest_other.update_parent(curr, curr.cost + dist)\n                                if (nearest_other.parent, nearest_other) not in edges:\n                                    edges.append((nearest_other.parent, nearest_other))\n                        return nearest_other\n                    else:\n                        return None\n                # extend nearest_other toward curr incrementally\n                new_pos = steer(nearest_other.position, curr.position, self.base_step)\n                if self._is_in_obstacle(new_pos, obstacles, is_3d) or not collision_free_edge(nearest_other.position, new_pos):\n                    return None\n                dist_step = math.dist(nearest_other.position, new_pos)\n                new_node = Node(new_pos)\n                neighbors = near_nodes(tree_other, new_pos, adaptive_radius(len(tree_other)))\n                min_cost = nearest_other.cost + dist_step\n                best_parent = nearest_other\n                # Find best parent among neighbors\n                for neighbor in neighbors:\n                    cost_try = neighbor.cost + math.dist(neighbor.position, new_pos)\n                    if cost_try < min_cost and collision_free_edge(neighbor.position, new_pos):\n                        min_cost = cost_try\n                        best_parent = neighbor\n                new_node.parent = best_parent\n                new_node.cost = min_cost\n                best_parent.add_child(new_node)\n                edges.append((best_parent, new_node))\n                tree_other.append(new_node)\n                nodes.append(new_node)\n\n                # Rewire neighbors if cheaper through new_node\n                for neighbor in neighbors:\n                    if neighbor == best_parent:\n                        continue\n                    new_cost = new_node.cost + math.dist(new_node.position, neighbor.position)\n                    if new_cost < neighbor.cost and collision_free_edge(new_node.position, neighbor.position):\n                        neighbor.update_parent(new_node, new_cost)\n                        if (neighbor.parent, neighbor) not in edges:\n                            edges.append((neighbor.parent, neighbor))\n\n                nearest_other = new_node\n                curr = curr\n\n        def near_nodes(tree, position, radius):\n            return [node for node in tree if math.dist(node.position, position) <= radius]\n\n        def path_smoothing(path):\n            # Shortcut smoothing by checking collisions between random pairs\n            if len(path) < 3:\n                return path\n            import random\n            refined = path[:]\n            for _ in range(100):\n                if len(refined) < 3:\n                    break\n                i = random.randint(0, len(refined) - 3)\n                j = random.randint(i + 2, len(refined) - 1)\n                if not collision_free_edge(refined[i], refined[j]):\n                    continue\n                # shortcut between refined[i] and refined[j]\n                refined = refined[:i+1] + refined[j:]\n            return refined\n\n        def reconstruct_path(node_start, node_goal):\n            path_start = node_start.path_from_root()\n            path_goal = node_goal.path_from_root()\n            return path_start + path_goal[::-1]\n\n        for iter_num in range(self.max_iter):\n            if time.monotonic() - start_time > time_limit:\n                # Time limit reached, return best found path\n                return PlannerResult(success, best_path, nodes, edges)\n\n            # Alternate trees on each iteration\n            tree_a, tree_b = (tree_start, tree_goal) if iter_num % 2 == 0 else (tree_goal, tree_start)\n            nodes_a_count = len(tree_a)\n            radius = adaptive_radius(nodes_a_count)\n\n            # Sampling with goal bias\n            if random.random() < self.goal_sample_rate:\n                rnd = goal_pos if tree_a is tree_start else start_pos\n                if not self._is_in_obstacle(rnd, obstacles, is_3d):\n                    sample = rnd\n                else:\n                    sample = informed_sample()\n            else:\n                sample = informed_sample()\n\n            nearest = min(tree_a, key=lambda n: math.dist(n.position, sample))\n            dist_to_sample = math.dist(nearest.position, sample)\n            if dist_to_sample == 0:\n                continue\n            step = min(self.base_step, dist_to_sample)\n\n            new_pos = steer(nearest.position, sample, step)\n            if self._is_in_obstacle(new_pos, obstacles, is_3d) or not collision_free_edge(nearest.position, new_pos):\n                continue\n\n            new_node = Node(new_pos)\n            neighbors = near_nodes(tree_a, new_pos, radius)\n            min_cost = nearest.cost + math.dist(nearest.position, new_pos)\n            best_parent = nearest\n\n            for nb in neighbors:\n                cost_try = nb.cost + math.dist(nb.position, new_pos)\n                if cost_try < min_cost and collision_free_edge(nb.position, new_pos):\n                    min_cost = cost_try\n                    best_parent = nb\n\n            best_parent.add_child(new_node)\n            new_node.cost = min_cost\n            tree_a.append(new_node)\n            nodes.append(new_node)\n            edges.append((best_parent, new_node))\n\n            # Rewire neighbors around new node\n            for nb in neighbors:\n                if nb == best_parent:\n                    continue\n                new_cost = new_node.cost + math.dist(new_node.position, nb.position)\n                if new_cost < nb.cost and collision_free_edge(new_node.position, nb.position):\n                    nb.update_parent(new_node, new_cost)\n                    if (nb.parent, nb) not in edges:\n                        edges.append((nb.parent, nb))\n\n            # Attempt to connect trees incrementally\n            conn_node = try_connect_trees(new_node, tree_b, nodes, edges)\n            if conn_node:\n                candidate_path = reconstruct_path(new_node, conn_node)\n                candidate_cost = new_node.cost + conn_node.cost\n                if candidate_cost < c_best:\n                    c_best = candidate_cost\n                    # Smooth path progressively on found solution\n                    best_path = path_smoothing(candidate_path)\n                    success = True\n                    # If path is short enough, early exit\n                    if c_best <= c_min * 1.01:\n                        break\n\n        if not success and best_path:\n            # Attempt final smoothing on last best path\n            best_path = path_smoothing(best_path)\n\n        return PlannerResult(success=success, path=best_path, nodes=nodes, edges=edges)\n\n    def _is_in_obstacle(self, pos, obstacles, is_3d):\n        for obs in obstacles:\n            if is_3d:\n                x, y, z, w, h, d = obs\n                px, py, pz = pos\n                if x <= px <= x + w and y <= py <= y + h and z <= pz <= z + d:\n                    return True\n            else:\n                x, y, w, h = obs\n                px, py = pos\n                if x <= px <= x + w and y <= py <= y + h:\n                    return True\n        return False\n\n    def _is_edge_in_obstacle(self, from_pos, to_pos, obstacles, is_3d, resolution=1.0):\n        import math\n        distance = math.dist(from_pos, to_pos)\n        steps = max(2, int(distance / resolution))\n        for i in range(steps + 1):\n            interp = tuple(from_pos[d] + (to_pos[d] - from_pos[d]) * i / steps for d in range(len(from_pos)))\n            if self._is_in_obstacle(interp, obstacles, is_3d):\n                return True\n        return False\n\n\nfrom typing import NamedTuple, List, Tuple\nclass PlannerResult(NamedTuple):\n    success: bool\n    path: List[Tuple[float, ...]]\n    nodes: List[Node]\n    edges: List[Tuple[Node, Node]]\n```')